In [4]:
# 05-monitoring-deployment.ipynb
# Customer Lifetime Value Prediction - Deployment & Monitoring
# GKE deployment, Cloud Run demo, Evidently AI, Cloud Functions

# Imports
from google.cloud import aiplatform
from google.cloud import storage
import pandas as pd
import numpy as np
import os

# Configuration
PROJECT_ID = "clv-predictions-mlops"
REGION = "us-central1"
BUCKET_NAME = "clv-prediction-data"

# Initialize Vertex AI
aiplatform.init(project=PROJECT_ID, location=REGION)

print(f"Project: {PROJECT_ID}")
print(f"Region: {REGION}")
print("="*50)
print("This notebook covers:")
print("  1. GKE deployment (screenshots)")
print("  2. Cloud Run demo app")
print("  3. Evidently AI drift monitoring")
print("  4. Cloud Functions retraining trigger")

Project: clv-predictions-mlops
Region: us-central1
This notebook covers:
  1. GKE deployment (screenshots)
  2. Cloud Run demo app
  3. Evidently AI drift monitoring
  4. Cloud Functions retraining trigger


In [6]:
# ============================================================
# PART 1: GKE DEPLOYMENT
# ============================================================

# Enable required APIs
!gcloud services enable container.googleapis.com --project={PROJECT_ID}

# Create GKE Autopilot cluster (simpler, auto-scales)
# Try us-east1 instead
!gcloud container clusters create-auto clv-prediction-cluster \
    --region=us-east1 \
    --project=clv-predictions-mlops

print("Cluster created!")

Creating cluster clv-prediction-cluster in us-east1... Cluster is being configu
red...⠶                                                                        
Creating cluster clv-prediction-cluster in us-east1... Cluster is being deploye
d...⠹                                                                          
Creating cluster clv-prediction-cluster in us-east1... Cluster is being health-
checked (Kubernetes Control Plane is healthy)...done.                          
Created [https://container.googleapis.com/v1/projects/clv-predictions-mlops/zones/us-east1/clusters/clv-prediction-cluster].
To inspect the contents of your cluster, go to: https://console.cloud.google.com/kubernetes/workload_/gcloud/us-east1/clv-prediction-cluster?project=clv-predictions-mlops
CRITICAL: ACTION REQUIRED: gke-gcloud-auth-plugin, which is needed for continued use of kubectl, was not found or is not executable. Install gke-gcloud-auth-plugin for use with kubectl by following https://cloud.google.com/k

In [8]:
!sudo apt-get update -qq
!sudo apt-get install -y google-cloud-cli-gke-gcloud-auth-plugin -qq

# Then get credentials
!gcloud container clusters get-credentials clv-prediction-cluster \
    --region=us-east1 \
    --project=clv-predictions-mlops

print("kubectl configured!")

Selecting previously unselected package google-cloud-cli-gke-gcloud-auth-plugin.
(Reading database ... 145187 files and directories currently installed.)
Preparing to unpack .../google-cloud-cli-gke-gcloud-auth-plugin_549.0.1-0_amd64.deb ...
Unpacking google-cloud-cli-gke-gcloud-auth-plugin (549.0.1-0) ...
Setting up google-cloud-cli-gke-gcloud-auth-plugin (549.0.1-0) ...
Fetching cluster endpoint and auth data.
kubeconfig entry generated for clv-prediction-cluster.
kubectl configured!


In [9]:
# Verify kubectl works
!kubectl get nodes

print("\nCluster ready for deployment!")


NAME                                                  STATUS   ROLES    AGE     VERSION
gk3-clv-prediction-clust-default-pool-e874a72a-wfpp   Ready    <none>   3m14s   v1.33.5-gke.1308000

Cluster ready for deployment!


In [10]:
# Create Kubernetes deployment manifest
deployment_yaml = """
apiVersion: apps/v1
kind: Deployment
metadata:
  name: clv-prediction-model
spec:
  replicas: 1
  selector:
    matchLabels:
      app: clv-model
  template:
    metadata:
      labels:
        app: clv-model
    spec:
      containers:
      - name: tf-serving
        image: tensorflow/serving:latest
        ports:
        - containerPort: 8501
        env:
        - name: MODEL_NAME
          value: "clv_model"
        volumeMounts:
        - name: model-volume
          mountPath: /models/clv_model
      volumes:
      - name: model-volume
        emptyDir: {}
---
apiVersion: v1
kind: Service
metadata:
  name: clv-prediction-service
spec:
  type: LoadBalancer
  ports:
  - port: 80
    targetPort: 8501
  selector:
    app: clv-model
"""

with open('deployment.yaml', 'w') as f:
    f.write(deployment_yaml)

print("Deployment manifest created")

# Apply to cluster
!kubectl apply -f deployment.yaml

print("\nDeployment started!")

Deployment manifest created
deployment.apps/clv-prediction-model created
service/clv-prediction-service created

Deployment started!


In [11]:
# Wait for deployment to be ready
!kubectl get deployments
!kubectl get pods
!kubectl get services

print("\nWaiting for external IP...")

NAME                   READY   UP-TO-DATE   AVAILABLE   AGE
clv-prediction-model   0/1     1            0           29s
NAME                                    READY   STATUS    RESTARTS   AGE
clv-prediction-model-79944bf798-xd4q5   0/1     Pending   0          29s
NAME                     TYPE           CLUSTER-IP       EXTERNAL-IP   PORT(S)        AGE
clv-prediction-service   LoadBalancer   34.118.237.179   <pending>     80:30488/TCP   30s
kubernetes               ClusterIP      34.118.224.1     <none>        443/TCP        8m11s

Waiting for external IP...


In [14]:
import time
time.sleep(60)

!kubectl get pods
!kubectl get services

NAME                                    READY   STATUS    RESTARTS   AGE
clv-prediction-model-79944bf798-xd4q5   1/1     Running   0          6m5s
NAME                     TYPE           CLUSTER-IP       EXTERNAL-IP     PORT(S)        AGE
clv-prediction-service   LoadBalancer   34.118.237.179   34.26.196.169   80:30488/TCP   6m6s
kubernetes               ClusterIP      34.118.224.1     <none>          443/TCP        13m


In [15]:
# Delete GKE cluster
!gcloud container clusters delete clv-prediction-cluster \
    --region=us-east1 \
    --project=clv-predictions-mlops \
    --quiet

print("Cluster deleted!")

Deleting cluster clv-prediction-cluster...done.                                
Deleted [https://container.googleapis.com/v1/projects/clv-predictions-mlops/zones/us-east1/clusters/clv-prediction-cluster].
Cluster deleted!


In [16]:
# ============================================================
# PART 2: CLOUD RUN DEMO APP
# ============================================================

# Create app directory
!mkdir -p streamlit_app

print("Creating Streamlit app files...")

Creating Streamlit app files...


In [19]:
# Create the Streamlit app with BigQuery logging
app_code = '''
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import tensorflow as tf
import joblib
from google.cloud import storage, bigquery
from datetime import datetime
import os

st.set_page_config(page_title="CLV Prediction MLOps", layout="wide")

# Initialize BigQuery client for logging
@st.cache_resource
def get_bq_client():
    try:
        return bigquery.Client(project="clv-predictions-mlops")
    except:
        return None

bq_client = get_bq_client()

def log_prediction(features_dict, prediction):
    """Log prediction to BigQuery for monitoring"""
    if bq_client is None:
        return
    try:
        table_id = "clv-predictions-mlops.retail_data.prediction_logs"
        row = {
            "timestamp": datetime.utcnow().isoformat(),
            "recency": features_dict.get("recency", 0),
            "frequency": features_dict.get("frequency", 0),
            "monetary": features_dict.get("monetary", 0),
            "prediction": float(prediction)
        }
        errors = bq_client.insert_rows_json(table_id, [row])
        if errors:
            print(f"BigQuery logging error: {errors}")
    except Exception as e:
        print(f"Logging failed: {e}")

# Load model and scaler from GCS
@st.cache_resource
def load_artifacts():
    try:
        client = storage.Client()
        bucket = client.bucket("clv-prediction-data")
        
        # Download model
        bucket.blob("models/clv_model_tuned.keras").download_to_filename("/tmp/model.keras")
        model = tf.keras.models.load_model("/tmp/model.keras")
        
        # Download scaler
        bucket.blob("models/clv_scaler.pkl").download_to_filename("/tmp/scaler.pkl")
        scaler = joblib.load("/tmp/scaler.pkl")
        
        return model, scaler
    except Exception as e:
        st.error(f"Could not load model: {e}")
        return None, None

model, scaler = load_artifacts()

# Sidebar
st.sidebar.header("Model Info")
st.sidebar.metric("Model Type", "Hybrid NN")
st.sidebar.metric("Best MAE", "$1,449")
st.sidebar.metric("Improvement", "27%")

st.sidebar.markdown("---")
st.sidebar.markdown("### Features")
st.sidebar.markdown("""
- 12 numerical features (RFM+)
- 384 text embeddings (Hugging Face)
- Tuned via Vertex AI Vizier
""")

# Main content
st.title("Customer Lifetime Value Prediction")
st.markdown("**MLOps Pipeline Demo** - Hybrid Neural Network with Hugging Face Embeddings")

tab1, tab2, tab3, tab4 = st.tabs(["Predict CLV", "Model Performance", "Feature Importance", "Architecture"])

with tab1:
    st.header("Predict Customer Lifetime Value")
    
    col1, col2 = st.columns(2)
    
    with col1:
        st.subheader("Customer Features")
        
        recency = st.slider("Recency (days since last purchase)", 0, 365, 30)
        frequency = st.slider("Frequency (number of orders)", 1, 50, 5)
        monetary = st.number_input("Monetary (total spend $)", 0, 50000, 500)
        avg_order = st.number_input("Average Order Value $", 0, 5000, 100)
        tenure = st.slider("Customer Tenure (days)", 0, 365, 180)
        unique_products = st.slider("Unique Products Purchased", 1, 100, 10)
    
    with col2:
        st.subheader("Prediction")
        
        if st.button("Predict CLV", type="primary"):
            if model is not None:
                # Create feature vector (simplified - using zeros for embeddings)
                features = np.zeros(396)
                features[0] = recency
                features[1] = frequency
                features[2] = monetary
                features[3] = avg_order
                features[4] = tenure
                features[5] = unique_products
                
                # Scale and predict
                features_scaled = scaler.transform(features.reshape(1, -1))
                prediction = model.predict(features_scaled, verbose=0)[0][0]
                prediction = max(0, prediction)
                
                # Log to BigQuery
                log_prediction({
                    "recency": recency,
                    "frequency": frequency,
                    "monetary": monetary
                }, prediction)
                
                st.metric("Predicted 12-Month CLV", f"${prediction:,.0f}")
                
                # Customer segment
                if prediction > 5000:
                    st.success("🌟 High-Value Customer")
                elif prediction > 1000:
                    st.info("📈 Medium-Value Customer")
                else:
                    st.warning("📊 Low-Value Customer")
            else:
                # Demo mode
                prediction = monetary * 1.5 + frequency * 100
                st.metric("Predicted 12-Month CLV (Demo)", f"${prediction:,.0f}")

with tab2:
    st.header("Model Performance")
    
    col1, col2 = st.columns(2)
    
    with col1:
        # Tuning results
        tuning_data = {
            "Model": ["Baseline", "Tuned"],
            "MAE ($)": [1987, 1449]
        }
        fig = px.bar(tuning_data, x="Model", y="MAE ($)", 
                     title="Hyperparameter Tuning Impact",
                     color="Model", color_discrete_map={"Baseline": "gray", "Tuned": "green"})
        st.plotly_chart(fig, use_container_width=True)
    
    with col2:
        # Metrics comparison
        st.markdown("### Performance Metrics")
        st.markdown("""
        | Metric | Baseline | Tuned | Improvement |
        |--------|----------|-------|-------------|
        | MAE | $1,987 | $1,449 | **27%** |
        | R² | 0.104 | 0.15+ | **~50%** |
        """)
        
        st.markdown("### Vizier Tuning")
        st.markdown("""
        - **Trials**: 15
        - **Algorithm**: Random Search
        - **Best params**: 201/74 units, 0.25 dropout, 0.0027 lr
        """)

with tab3:
    st.header("Feature Importance (Integrated Gradients)")
    
    importance_data = {
        "Feature": ["monetary", "unique_purchase_days", "frequency", "orders_per_month", 
                   "total_items_purchased", "unique_products", "avg_order_value", 
                   "customer_tenure_days", "emb_115", "emb_279"],
        "Attribution": [1900, 1350, 1300, 1150, 1100, 1000, 250, 220, 150, 140]
    }
    
    fig = px.bar(importance_data, x="Attribution", y="Feature", orientation="h",
                 title="Top Features Driving CLV Predictions",
                 color="Attribution", color_continuous_scale="greens")
    fig.update_layout(yaxis={"categoryorder": "total ascending"})
    st.plotly_chart(fig, use_container_width=True)
    
    st.markdown("""
    **Key Insights:**
    - **Monetary** (past spend) is the strongest predictor
    - **Engagement metrics** (purchase frequency, unique days) rank highly
    - **Text embeddings** (emb_*) contribute - what customers buy matters
    """)

with tab4:
    st.header("MLOps Architecture")
    
    st.code("""
                         CLV PREDICTION PIPELINE
    
    ┌─────────────┐     ┌─────────────┐     ┌─────────────┐
    │   BigQuery  │────▶│   Dataproc  │────▶│  Hugging    │
    │  (Raw Data) │     │  (PySpark)  │     │   Face      │
    └─────────────┘     └─────────────┘     └─────────────┘
                                                   │
                                                   ▼
    ┌─────────────┐     ┌─────────────┐     ┌─────────────┐
    │   Vertex    │◀────│   Vertex    │◀────│    GCS      │
    │   Vizier    │     │  Pipeline   │     │ (Features)  │
    └─────────────┘     └─────────────┘     └─────────────┘
           │                   │
           ▼                   ▼
    ┌─────────────┐     ┌─────────────┐     ┌─────────────┐
    │   Model     │────▶│  Cloud Run  │────▶│  BigQuery   │
    │  Registry   │     │   (Demo)    │     │  (Logging)  │
    └─────────────┘     └─────────────┘     └─────────────┘
                               │
                               ▼
                        ┌─────────────┐
                        │  Evidently  │
                        │     AI      │
                        └─────────────┘
    """, language=None)
    
    col1, col2, col3 = st.columns(3)
    
    with col1:
        st.markdown("**Data Layer**")
        st.markdown("- BigQuery (storage)\\n- PySpark (processing)\\n- Hugging Face (embeddings)")
    
    with col2:
        st.markdown("**ML Layer**")
        st.markdown("- Hybrid NN (TensorFlow)\\n- Vizier (tuning)\\n- Vertex Pipelines")
    
    with col3:
        st.markdown("**Monitoring**")
        st.markdown("- BigQuery (prediction logs)\\n- Evidently AI (drift)\\n- Cloud Functions (retrain)")

# Footer
st.markdown("---")
st.markdown("**Project by Arion Farhi** | [GitHub](https://github.com/arion-farhi)")
'''

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Created: streamlit_app/app.py")

Created: streamlit_app/app.py


In [20]:
# Create requirements.txt
requirements = """
streamlit==1.28.0
pandas==2.0.3
numpy==1.24.3
plotly==5.17.0
tensorflow==2.15.0
joblib==1.3.2
google-cloud-storage==2.12.0
"""

with open("streamlit_app/requirements.txt", "w") as f:
    f.write(requirements.strip())

# Create Dockerfile
dockerfile = """
FROM python:3.10-slim

WORKDIR /app

COPY requirements.txt .
RUN pip install --no-cache-dir -r requirements.txt

COPY app.py .

EXPOSE 8080

CMD ["streamlit", "run", "app.py", "--server.port=8080", "--server.address=0.0.0.0"]
"""

with open("streamlit_app/Dockerfile", "w") as f:
    f.write(dockerfile.strip())

print("Created:")
print("  - streamlit_app/requirements.txt")
print("  - streamlit_app/Dockerfile")


Created:
  - streamlit_app/requirements.txt
  - streamlit_app/Dockerfile


In [21]:
# Create BigQuery table for prediction logs
!bq mk --table \
    clv-predictions-mlops:retail_data.prediction_logs \
    timestamp:TIMESTAMP,recency:INTEGER,frequency:INTEGER,monetary:FLOAT,prediction:FLOAT

print("Created prediction_logs table")

Table 'clv-predictions-mlops:retail_data.prediction_logs' successfully created.
Created prediction_logs table


In [25]:
!gcloud services enable cloudbuild.googleapis.com --project={PROJECT_ID}

In [27]:
# Grant Cloud Build permissions
!gcloud projects add-iam-policy-binding {PROJECT_ID} \
    --member="serviceAccount:674754622820-compute@developer.gserviceaccount.com" \
    --role="roles/cloudbuild.builds.builder"

!gcloud projects add-iam-policy-binding {PROJECT_ID} \
    --member="serviceAccount:674754622820-compute@developer.gserviceaccount.com" \
    --role="roles/storage.admin"

print("Permissions granted. Retrying build...")

ERROR: (gcloud.projects.add-iam-policy-binding) [674754622820-compute@developer.gserviceaccount.com] does not have permission to access projects instance [clv-predictions-mlops:setIamPolicy] (or it may not exist): Policy update access denied. This command is authenticated as 674754622820-compute@developer.gserviceaccount.com which is the active account specified by the [core/account] property.
ERROR: (gcloud.projects.add-iam-policy-binding) [674754622820-compute@developer.gserviceaccount.com] does not have permission to access projects instance [clv-predictions-mlops:setIamPolicy] (or it may not exist): Policy update access denied. This command is authenticated as 674754622820-compute@developer.gserviceaccount.com which is the active account specified by the [core/account] property.
Permissions granted. Retrying build...


In [28]:
# Build and deploy to Cloud Run

# Enable Cloud Run API
!gcloud services enable run.googleapis.com --project={PROJECT_ID}

# Build container image
!gcloud builds submit streamlit_app \
    --tag gcr.io/{PROJECT_ID}/clv-demo \
    --project={PROJECT_ID}

print("Container built!")


Creating temporary archive of 3 file(s) totalling 9.6 KiB before compression.
Uploading tarball of [streamlit_app] to [gs://clv-predictions-mlops_cloudbuild/source/1765483241.157256-2e13f1b7721e4870b895d1a406808ecf.tgz]
Created [https://cloudbuild.googleapis.com/v1/projects/clv-predictions-mlops/locations/global/builds/5a29cfe1-6853-4f44-afed-8ecb1b2d9a1a].
Logs are available at [ https://console.cloud.google.com/cloud-build/builds/5a29cfe1-6853-4f44-afed-8ecb1b2d9a1a?project=674754622820 ].
Waiting for build to complete. Polling interval: 1 second(s).
----------------------------- REMOTE BUILD OUTPUT ------------------------------
starting build "5a29cfe1-6853-4f44-afed-8ecb1b2d9a1a"

FETCHSOURCE
Fetching storage object: gs://clv-predictions-mlops_cloudbuild/source/1765483241.157256-2e13f1b7721e4870b895d1a406808ecf.tgz#1765483241332425
Copying gs://clv-predictions-mlops_cloudbuild/source/1765483241.157256-2e13f1b7721e4870b895d1a406808ecf.tgz#1765483241332425...
/ [1 files][  3.4 KiB/ 

In [29]:
# Deploy to Cloud Run
!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --platform managed \
    --region {REGION} \
    --allow-unauthenticated \
    --memory 2Gi \
    --project={PROJECT_ID}

print("Save as: cloud-run.png")

Deploying container to Cloud Run service [clv-demo] in project [clv-predictions-mlops] region [us-central1]
Deploying new service...                                                       
  . Creating Revision...                                                       
  . Routing traffic...                                                         
  . Setting IAM Policy...                                                      
  Deploying new service...                                                     



⠛ Deploying new service...                                                     



⠹ Deploying new service...                                                     



⠼ Deploying new service...                                                     



⠶ Deploying new service...                                                     


  ⠶ Setting IAM Policy...                                                      
⠧ Deploying new service...                                                    

In [34]:
# Update requirements.txt with sklearn
requirements = """
streamlit==1.28.0
pandas==2.0.3
numpy==1.24.3
plotly==5.17.0
tensorflow==2.17.0
joblib==1.3.2
google-cloud-storage==2.12.0
google-cloud-bigquery==3.12.0
scikit-learn==1.3.0
"""

with open("streamlit_app/requirements.txt", "w") as f:
    f.write(requirements.strip())

print("Added scikit-learn")

Added scikit-learn


In [35]:
# Rebuild and redeploy
!gcloud builds submit streamlit_app \
    --tag gcr.io/{PROJECT_ID}/clv-demo \
    --project={PROJECT_ID}

!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --platform managed \
    --region {REGION} \
    --allow-unauthenticated \
    --memory 2Gi \
    --project={PROJECT_ID}

Creating temporary archive of 3 file(s) totalling 9.7 KiB before compression.
Uploading tarball of [streamlit_app] to [gs://clv-predictions-mlops_cloudbuild/source/1765484718.697734-8b2a14fc7e0241af88a88ec7b1948f5d.tgz]
Created [https://cloudbuild.googleapis.com/v1/projects/clv-predictions-mlops/locations/global/builds/2198bec0-ecec-4e8b-9119-dc1cb599812e].
Logs are available at [ https://console.cloud.google.com/cloud-build/builds/2198bec0-ecec-4e8b-9119-dc1cb599812e?project=674754622820 ].
Waiting for build to complete. Polling interval: 1 second(s).
----------------------------- REMOTE BUILD OUTPUT ------------------------------
starting build "2198bec0-ecec-4e8b-9119-dc1cb599812e"

FETCHSOURCE
Fetching storage object: gs://clv-predictions-mlops_cloudbuild/source/1765484718.697734-8b2a14fc7e0241af88a88ec7b1948f5d.tgz#1765484718920822
Copying gs://clv-predictions-mlops_cloudbuild/source/1765484718.697734-8b2a14fc7e0241af88a88ec7b1948f5d.tgz#1765484718920822...
/ [1 files][  3.4 KiB/ 

In [36]:
# Update app.py with formula-based demo prediction
app_code = open("streamlit_app/app.py").read()

old_prediction = '''                # Scale and predict
                features_scaled = scaler.transform(features.reshape(1, -1))
                prediction = model.predict(features_scaled, verbose=0)[0][0]
                prediction = max(0, prediction)'''

new_prediction = '''                # Demo prediction based on RFM logic
                # Real model needs full 396 features including embeddings
                # This formula approximates realistic CLV for demo purposes
                recency_factor = max(0, (365 - recency) / 365)  # Recent = higher
                prediction = (monetary * 1.2) + (frequency * 150) + (recency_factor * 500) + (tenure / 365 * 300)
                prediction = max(0, prediction)'''

app_code = app_code.replace(old_prediction, new_prediction)

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Updated to formula-based demo prediction")

Updated to formula-based demo prediction


In [37]:
!gcloud builds submit streamlit_app \
    --tag gcr.io/{PROJECT_ID}/clv-demo \
    --project={PROJECT_ID}

!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --platform managed \
    --region {REGION} \
    --allow-unauthenticated \
    --memory 2Gi \
    --project={PROJECT_ID}

Creating temporary archive of 3 file(s) totalling 9.9 KiB before compression.
Uploading tarball of [streamlit_app] to [gs://clv-predictions-mlops_cloudbuild/source/1765485455.088854-fd6d55a9859549f29948331b553781c7.tgz]
Created [https://cloudbuild.googleapis.com/v1/projects/clv-predictions-mlops/locations/global/builds/e4151590-8d4c-4689-a650-0bb3b239bedf].
Logs are available at [ https://console.cloud.google.com/cloud-build/builds/e4151590-8d4c-4689-a650-0bb3b239bedf?project=674754622820 ].
Waiting for build to complete. Polling interval: 1 second(s).
----------------------------- REMOTE BUILD OUTPUT ------------------------------
starting build "e4151590-8d4c-4689-a650-0bb3b239bedf"

FETCHSOURCE
Fetching storage object: gs://clv-predictions-mlops_cloudbuild/source/1765485455.088854-fd6d55a9859549f29948331b553781c7.tgz#1765485455269877
Copying gs://clv-predictions-mlops_cloudbuild/source/1765485455.088854-fd6d55a9859549f29948331b553781c7.tgz#1765485455269877...
/ [1 files][  3.5 KiB/ 

In [39]:
# Update app.py to use real feature baseline
app_code = '''
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import tensorflow as tf
import joblib
from google.cloud import storage, bigquery
from datetime import datetime
import os

st.set_page_config(page_title="CLV Prediction MLOps", layout="wide")

# Initialize BigQuery client for logging
@st.cache_resource
def get_bq_client():
    try:
        return bigquery.Client(project="clv-predictions-mlops")
    except:
        return None

bq_client = get_bq_client()

def log_prediction(features_dict, prediction):
    """Log prediction to BigQuery for monitoring"""
    if bq_client is None:
        return
    try:
        table_id = "clv-predictions-mlops.retail_data.prediction_logs"
        row = {
            "timestamp": datetime.utcnow().isoformat(),
            "recency": features_dict.get("recency", 0),
            "frequency": features_dict.get("frequency", 0),
            "monetary": features_dict.get("monetary", 0),
            "prediction": float(prediction)
        }
        errors = bq_client.insert_rows_json(table_id, [row])
    except Exception as e:
        pass

# Load model, scaler, and baseline features from GCS
@st.cache_resource
def load_artifacts():
    try:
        client = storage.Client()
        bucket = client.bucket("clv-prediction-data")
        
        # Download model
        bucket.blob("models/clv_model_tuned.keras").download_to_filename("/tmp/model.keras")
        model = tf.keras.models.load_model("/tmp/model.keras")
        
        # Download scaler
        bucket.blob("models/clv_scaler.pkl").download_to_filename("/tmp/scaler.pkl")
        scaler = joblib.load("/tmp/scaler.pkl")
        
        # Download feature data for baseline
        bucket.blob("features/clv_features.parquet").download_to_filename("/tmp/features.parquet")
        df = pd.read_parquet("/tmp/features.parquet")
        feature_cols = [c for c in df.columns if c not in ["customer_id", "target_clv"]]
        baseline = df[feature_cols].median().values  # Median customer as baseline
        
        return model, scaler, baseline, feature_cols
    except Exception as e:
        st.error(f"Could not load model: {e}")
        return None, None, None, None

model, scaler, baseline_features, feature_cols = load_artifacts()

# Sidebar
st.sidebar.header("Model Info")
st.sidebar.metric("Model Type", "Hybrid NN")
st.sidebar.metric("Best MAE", "$1,449")
st.sidebar.metric("Improvement", "27%")

st.sidebar.markdown("---")
st.sidebar.markdown("### Features")
st.sidebar.markdown("""
- 12 numerical features (RFM+)
- 384 text embeddings (Hugging Face)
- Tuned via Vertex AI Vizier
""")

# Main content
st.title("Customer Lifetime Value Prediction")
st.markdown("**MLOps Pipeline Demo** - Hybrid Neural Network with Hugging Face Embeddings")

tab1, tab2, tab3, tab4 = st.tabs(["Predict CLV", "Model Performance", "Feature Importance", "Architecture"])

with tab1:
    st.header("Predict Customer Lifetime Value")
    
    col1, col2 = st.columns(2)
    
    with col1:
        st.subheader("Customer Features")
        
        recency = st.slider("Recency (days since last purchase)", 0, 365, 30)
        frequency = st.slider("Frequency (number of orders)", 1, 50, 5)
        monetary = st.number_input("Monetary (total spend $)", 0, 50000, 500)
        avg_order = st.number_input("Average Order Value $", 0, 5000, 100)
        tenure = st.slider("Customer Tenure (days)", 0, 365, 180)
        unique_products = st.slider("Unique Products Purchased", 1, 100, 10)
    
    with col2:
        st.subheader("Prediction")
        
        if st.button("Predict CLV", type="primary"):
            if model is not None and baseline_features is not None:
                # Start with median customer baseline (includes real embeddings)
                features = baseline_features.copy()
                
                # Override with slider values
                if "recency" in feature_cols:
                    features[feature_cols.index("recency")] = recency
                if "frequency" in feature_cols:
                    features[feature_cols.index("frequency")] = frequency
                if "monetary" in feature_cols:
                    features[feature_cols.index("monetary")] = monetary
                if "avg_order_value" in feature_cols:
                    features[feature_cols.index("avg_order_value")] = avg_order
                if "customer_tenure_days" in feature_cols:
                    features[feature_cols.index("customer_tenure_days")] = tenure
                if "unique_products" in feature_cols:
                    features[feature_cols.index("unique_products")] = unique_products
                
                # Scale and predict with ACTUAL model
                features_scaled = scaler.transform(features.reshape(1, -1))
                prediction = model.predict(features_scaled, verbose=0)[0][0]
                prediction = max(0, prediction)
                
                # Log to BigQuery
                log_prediction({
                    "recency": recency,
                    "frequency": frequency,
                    "monetary": monetary
                }, prediction)
                
                st.metric("Predicted 12-Month CLV", f"${prediction:,.0f}")
                
                # Customer segment
                if prediction > 5000:
                    st.success("🌟 High-Value Customer")
                elif prediction > 1000:
                    st.info("📈 Medium-Value Customer")
                else:
                    st.warning("📊 Low-Value Customer")
            else:
                st.error("Model not loaded")

with tab2:
    st.header("Model Performance")
    
    col1, col2 = st.columns(2)
    
    with col1:
        # Tuning results
        tuning_data = {
            "Model": ["Baseline", "Tuned"],
            "MAE ($)": [1987, 1449]
        }
        fig = px.bar(tuning_data, x="Model", y="MAE ($)", 
                     title="Hyperparameter Tuning Impact",
                     color="Model", color_discrete_map={"Baseline": "gray", "Tuned": "green"})
        st.plotly_chart(fig, use_container_width=True)
    
    with col2:
        # Metrics comparison
        st.markdown("### Performance Metrics")
        st.markdown("""
        | Metric | Baseline | Tuned | Improvement |
        |--------|----------|-------|-------------|
        | MAE | $1,987 | $1,449 | **27%** |
        | R² | 0.104 | 0.15+ | **~50%** |
        """)
        
        st.markdown("### Vizier Tuning")
        st.markdown("""
        - **Trials**: 15
        - **Algorithm**: Random Search
        - **Best params**: 201/74 units, 0.25 dropout, 0.0027 lr
        """)

with tab3:
    st.header("Feature Importance (Integrated Gradients)")
    
    importance_data = {
        "Feature": ["monetary", "unique_purchase_days", "frequency", "orders_per_month", 
                   "total_items_purchased", "unique_products", "avg_order_value", 
                   "customer_tenure_days", "emb_115", "emb_279"],
        "Attribution": [1900, 1350, 1300, 1150, 1100, 1000, 250, 220, 150, 140]
    }
    
    fig = px.bar(importance_data, x="Attribution", y="Feature", orientation="h",
                 title="Top Features Driving CLV Predictions",
                 color="Attribution", color_continuous_scale="greens")
    fig.update_layout(yaxis={"categoryorder": "total ascending"})
    st.plotly_chart(fig, use_container_width=True)
    
    st.markdown("""
    **Key Insights:**
    - **Monetary** (past spend) is the strongest predictor
    - **Engagement metrics** (purchase frequency, unique days) rank highly
    - **Text embeddings** (emb_*) contribute - what customers buy matters
    """)

with tab4:
    st.header("MLOps Architecture")
    
    st.code("""
                         CLV PREDICTION PIPELINE
    
    ┌─────────────┐     ┌─────────────┐     ┌─────────────┐
    │   BigQuery  │────▶│   Dataproc  │────▶│  Hugging    │
    │  (Raw Data) │     │  (PySpark)  │     │   Face      │
    └─────────────┘     └─────────────┘     └─────────────┘
                                                   │
                                                   ▼
    ┌─────────────┐     ┌─────────────┐     ┌─────────────┐
    │   Vertex    │◀────│   Vertex    │◀────│    GCS      │
    │   Vizier    │     │  Pipeline   │     │ (Features)  │
    └─────────────┘     └─────────────┘     └─────────────┘
           │                   │
           ▼                   ▼
    ┌─────────────┐     ┌─────────────┐     ┌─────────────┐
    │   Model     │────▶│  Cloud Run  │────▶│  BigQuery   │
    │  Registry   │     │   (Demo)    │     │  (Logging)  │
    └─────────────┘     └─────────────┘     └─────────────┘
                               │
                               ▼
                        ┌─────────────┐     ┌─────────────┐
                        │  Evidently  │────▶│   Cloud     │
                        │  AI (Drift) │     │  Functions  │
                        └─────────────┘     └─────────────┘
                                                   │
                                                   ▼
                                            ┌─────────────┐
                                            │  Retrain    │
                                            │  Pipeline   │
                                            └─────────────┘
    """, language=None)
    
    col1, col2, col3 = st.columns(3)
    
    with col1:
        st.markdown("**Data Layer**")
        st.markdown("- BigQuery (storage)\\n- PySpark (processing)\\n- Hugging Face (embeddings)")
    
    with col2:
        st.markdown("**ML Layer**")
        st.markdown("- Hybrid NN (TensorFlow)\\n- Vizier (tuning)\\n- Vertex Pipelines")
    
    with col3:
        st.markdown("**Monitoring**")
        st.markdown("- BigQuery (prediction logs)\\n- Evidently AI (drift)\\n- Cloud Functions (retrain)")

# Footer
st.markdown("---")
st.markdown("**Project by Arion Farhi** | [GitHub](https://github.com/arion-farhi)")
'''

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Updated app.py:")
print("  - Loads actual feature data as baseline (includes real embeddings)")
print("  - Overrides only the 6 slider values")
print("  - Uses REAL model for predictions")
print("  - Updated architecture diagram with Cloud Functions retraining")

Updated app.py:
  - Loads actual feature data as baseline (includes real embeddings)
  - Overrides only the 6 slider values
  - Uses REAL model for predictions
  - Updated architecture diagram with Cloud Functions retraining


In [40]:
# Update app.py with explanatory note
app_code = open("streamlit_app/app.py").read()

# Find the footer and add note before it
old_footer = '''# Footer
st.markdown("---")
st.markdown("**Project by Arion Farhi** | [GitHub](https://github.com/arion-farhi)")'''

new_footer = '''# Footer
st.markdown("---")
st.caption("📝 Note: This demo exposes 6 of 396 features. The model uses median customer values as baseline (including 384 Hugging Face text embeddings) and overrides with slider inputs for real-time prediction.")
st.markdown("**Project by Arion Farhi** | [GitHub](https://github.com/arion-farhi)")'''

app_code = app_code.replace(old_footer, new_footer)

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Added explanatory note to footer")

Added explanatory note to footer


In [41]:
!gcloud builds submit streamlit_app \
    --tag gcr.io/{PROJECT_ID}/clv-demo \
    --project={PROJECT_ID}

!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --platform managed \
    --region {REGION} \
    --allow-unauthenticated \
    --memory 2Gi \
    --project={PROJECT_ID}

Creating temporary archive of 3 file(s) totalling 11.3 KiB before compression.
Uploading tarball of [streamlit_app] to [gs://clv-predictions-mlops_cloudbuild/source/1765486122.478473-e4ccad75f71246d183c8cc81adc12f5d.tgz]
Created [https://cloudbuild.googleapis.com/v1/projects/clv-predictions-mlops/locations/global/builds/3b6a12ac-06da-4707-8dd1-4a2f48c434f0].
Logs are available at [ https://console.cloud.google.com/cloud-build/builds/3b6a12ac-06da-4707-8dd1-4a2f48c434f0?project=674754622820 ].
Waiting for build to complete. Polling interval: 1 second(s).
----------------------------- REMOTE BUILD OUTPUT ------------------------------
starting build "3b6a12ac-06da-4707-8dd1-4a2f48c434f0"

FETCHSOURCE
Fetching storage object: gs://clv-predictions-mlops_cloudbuild/source/1765486122.478473-e4ccad75f71246d183c8cc81adc12f5d.tgz#1765486122685103
Copying gs://clv-predictions-mlops_cloudbuild/source/1765486122.478473-e4ccad75f71246d183c8cc81adc12f5d.tgz#1765486122685103...
/ [1 files][  3.7 KiB/

In [42]:
# ============================================================
# PART 3: EVIDENTLY AI DRIFT MONITORING
# ============================================================

!pip install evidently -q

print("Evidently AI installed")

Evidently AI installed


In [44]:
!pip install sniffio anyio -q

In [50]:
# Download features first
!gsutil cp gs://{BUCKET_NAME}/features/clv_features.parquet /tmp/clv_features.parquet

Copying gs://clv-prediction-data/features/clv_features.parquet...
/ [1 files][  9.1 MiB/  9.1 MiB]                                                
Operation completed over 1 objects/9.1 MiB.                                      


In [51]:
from evidently import Report
from evidently.presets import DataDriftPreset

# Load feature data
df = pd.read_parquet('/tmp/clv_features.parquet')

# Split into reference (training) and current (simulated production)
reference_data = df.sample(frac=0.7, random_state=42)
current_data = df.drop(reference_data.index)

# Select key numerical features for drift monitoring (correct column names)
drift_features = ['recency_days', 'frequency', 'monetary', 'avg_order_value', 
                  'customer_tenure_days', 'unique_products', 'total_items_purchased',
                  'orders_per_month', 'unique_purchase_days', 'target_clv']

reference_subset = reference_data[drift_features]
current_subset = current_data[drift_features]

# Generate drift report
drift_report = Report([DataDriftPreset()])
drift_report.run(reference_data=reference_subset, current_data=current_subset)

# Save report
drift_report.save_html("evidently_drift_report.html")

print("Drift report saved: evidently_drift_report.html")

AttributeError: 'Report' object has no attribute 'save_html'

In [54]:
# Save the result
result.save_html("evidently_drift_report.html")

print("Drift report saved: evidently_drift_report.html")

Drift report saved: evidently_drift_report.html


In [58]:
# ============================================================
# PART 4: CLOUD FUNCTIONS RETRAINING TRIGGER
# ============================================================

!mkdir -p cloud_functions/retrain_trigger

# Create main.py
main_py = '''
import functions_framework
from google.cloud import aiplatform

@functions_framework.http
def trigger_retrain(request):
    """HTTP Cloud Function to trigger pipeline retraining."""
    
    # Initialize Vertex AI
    aiplatform.init(
        project="clv-predictions-mlops",
        location="us-central1"
    )
    
    # Submit pipeline job
    job = aiplatform.PipelineJob(
        display_name="clv-pipeline-retrain",
        template_path="gs://clv-prediction-data/pipeline_root/clv_pipeline.json",
        pipeline_root="gs://clv-prediction-data/pipeline_root",
        parameter_values={
            "bucket_name": "clv-prediction-data",
            "project_id": "clv-predictions-mlops",
            "region": "us-central1",
            "units_1": 201,
            "units_2": 74,
            "dropout": 0.2478,
            "learning_rate": 0.0027,
            "mae_threshold": 2500.0
        }
    )
    
    job.submit()
    
    return {"status": "Pipeline triggered", "job_name": job.display_name}
'''

with open("cloud_functions/retrain_trigger/main.py", "w") as f:
    f.write(main_py)

# Create requirements.txt
requirements = '''
functions-framework==3.*
google-cloud-aiplatform>=1.25.0
'''

with open("cloud_functions/retrain_trigger/requirements.txt", "w") as f:
    f.write(requirements.strip())

print("Created cloud_functions/retrain_trigger/")
print("  - main.py")
print("  - requirements.txt")

Created cloud_functions/retrain_trigger/
  - main.py
  - requirements.txt


In [59]:
# Enable Cloud Functions API and deploy
!gcloud services enable cloudfunctions.googleapis.com --project={PROJECT_ID}
!gcloud services enable cloudbuild.googleapis.com --project={PROJECT_ID}

# Upload pipeline JSON to GCS
!gsutil cp clv_pipeline.json gs://{BUCKET_NAME}/pipeline_root/

# Deploy Cloud Function
!gcloud functions deploy clv-retrain-trigger \
    --gen2 \
    --runtime=python310 \
    --region={REGION} \
    --source=cloud_functions/retrain_trigger \
    --entry-point=trigger_retrain \
    --trigger-http \
    --allow-unauthenticated \
    --project={PROJECT_ID}

print("Cloud Function deployed!")

Operation "operations/acf.p2-674754622820-0cb41dc0-f597-4db9-a087-d4d1a097e236" finished successfully.
Copying file://clv_pipeline.json [Content-Type=application/json]...
/ [1 files][ 19.4 KiB/ 19.4 KiB]                                                
Operation completed over 1 objects/19.4 KiB.                                     
Preparing function...done.                                                     
Deploying function...                                                          
  . [Build]                                                                    
  . [Service]                                                                  
  . [ArtifactRegistry]                                                         
  . [Healthcheck]                                                              
  . [Triggercheck]                                                             
  Deploying function...                                                        





⠛ Deploying function.

In [1]:
# ============================================================
# PART 5: CLOUD BUILD CI/CD
# ============================================================

cloudbuild_yaml = '''
steps:
  # Build the container image
  - name: 'gcr.io/cloud-builders/docker'
    args: ['build', '-t', 'gcr.io/$PROJECT_ID/clv-demo', './streamlit_app']

  # Push the container image to Container Registry
  - name: 'gcr.io/cloud-builders/docker'
    args: ['push', 'gcr.io/$PROJECT_ID/clv-demo']

  # Deploy to Cloud Run
  - name: 'gcr.io/google.com/cloudsdktool/cloud-sdk'
    entrypoint: gcloud
    args:
      - 'run'
      - 'deploy'
      - 'clv-demo'
      - '--image'
      - 'gcr.io/$PROJECT_ID/clv-demo'
      - '--region'
      - 'us-central1'
      - '--platform'
      - 'managed'
      - '--allow-unauthenticated'
      - '--memory'
      - '2Gi'

options:
  logging: CLOUD_LOGGING_ONLY
'''

with open("cloudbuild.yaml", "w") as f:
    f.write(cloudbuild_yaml.strip())

print("Created: cloudbuild.yaml")
print("\nThis enables automatic deployment when pushing to GitHub:")
print("  git push → Cloud Build → Build container → Deploy to Cloud Run")

Created: cloudbuild.yaml

This enables automatic deployment when pushing to GitHub:
  git push → Cloud Build → Build container → Deploy to Cloud Run


In [4]:
# ============================================================
# PART 6: A/B TESTING INFRASTRUCTURE (Traffic Splitting)
# ============================================================

# Cloud Run supports traffic splitting between revisions
# This creates a second revision and splits traffic

print("A/B Testing with Cloud Run Traffic Splitting")
print("=" * 50)
print("""
Cloud Run allows traffic splitting between model versions:

# Deploy new model version (creates new revision)
gcloud run deploy clv-demo --image gcr.io/PROJECT/clv-demo:v2

# Split traffic 90/10 between revisions
gcloud run services update-traffic clv-demo \\
    --region=us-central1 \\
    --to-revisions=clv-demo-v1=90,clv-demo-v2=10

# Gradually shift traffic as new model proves itself
gcloud run services update-traffic clv-demo \\
    --region=us-central1 \\
    --to-revisions=clv-demo-v1=50,clv-demo-v2=50

# Full rollout
gcloud run services update-traffic clv-demo \\
    --region=us-central1 \\
    --to-revisions=clv-demo-v2=100
""")

# Show current revisions
!gcloud run revisions list --service=clv-demo --region={REGION} --project={PROJECT_ID}

A/B Testing with Cloud Run Traffic Splitting

Cloud Run allows traffic splitting between model versions:

# Deploy new model version (creates new revision)
gcloud run deploy clv-demo --image gcr.io/PROJECT/clv-demo:v2

# Split traffic 90/10 between revisions
gcloud run services update-traffic clv-demo \
    --region=us-central1 \
    --to-revisions=clv-demo-v1=90,clv-demo-v2=10

# Gradually shift traffic as new model proves itself
gcloud run services update-traffic clv-demo \
    --region=us-central1 \
    --to-revisions=clv-demo-v1=50,clv-demo-v2=50

# Full rollout
gcloud run services update-traffic clv-demo \
    --region=us-central1 \
    --to-revisions=clv-demo-v2=100

   REVISION            ACTIVE  SERVICE   DEPLOYED                 DEPLOYED BY
✔  clv-demo-00006-ss4  yes     clv-demo  2025-12-11 20:52:55 UTC  674754622820-compute@developer.gserviceaccount.com
✔  clv-demo-00005-9nb          clv-demo  2025-12-11 20:42:15 UTC  674754622820-compute@developer.gserviceaccount.com
✔  clv

In [6]:
# Deploy v1
!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --region={REGION} \
    --platform=managed \
    --allow-unauthenticated \
    --memory=2Gi \
    --tag=model-v1 \
    --project={PROJECT_ID}

# Deploy v2 (creates new revision)
!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --region={REGION} \
    --platform=managed \
    --allow-unauthenticated \
    --memory=2Gi \
    --tag=model-v2 \
    --project={PROJECT_ID}

# Split traffic 80/20
!gcloud run services update-traffic clv-demo \
    --region={REGION} \
    --to-tags=model-v1=80,model-v2=20 \
    --project={PROJECT_ID}

# Show current traffic allocation
!gcloud run services describe clv-demo \
    --region={REGION} \
    --project={PROJECT_ID} \
    --format="value(status.traffic)"

print("\nTraffic split: 80% model-v1, 20% model-v2")

Deploying container to Cloud Run service [clv-demo] in project [clv-predictions-mlops] region [us-central1]
Deploying...                                                                   
  . Creating Revision...                                                       
  . Routing traffic...                                                         
  . Setting IAM Policy...                                                      
  Deploying...                                                                 



⠛ Deploying...                                                                 



⠹ Deploying...                                                                 


  ⠹ Setting IAM Policy...                                                      
⠼ Deploying...                                                                 


  ⠼ Setting IAM Policy...                                                      
⠶ Deploying...                                                                 




In [7]:
# ============================================================
# PART 7: EVIDENTLY + PUB/SUB DRIFT TRIGGER
# ============================================================

# Enable Pub/Sub API
!gcloud services enable pubsub.googleapis.com --project={PROJECT_ID}

# Create Pub/Sub topic for drift alerts
!gcloud pubsub topics create drift-detected --project={PROJECT_ID}

# Create subscription that triggers the Cloud Function
!gcloud pubsub subscriptions create drift-trigger-sub \
    --topic=drift-detected \
    --push-endpoint=https://clv-retrain-trigger-cpvl5opmca-uc.a.run.app \
    --project={PROJECT_ID}

print("Pub/Sub setup complete:")
print("  Topic: drift-detected")
print("  Subscription: drift-trigger-sub → triggers Cloud Function")

Created topic [projects/clv-predictions-mlops/topics/drift-detected].
Created subscription [projects/clv-predictions-mlops/subscriptions/drift-trigger-sub].
Pub/Sub setup complete:
  Topic: drift-detected
  Subscription: drift-trigger-sub → triggers Cloud Function


In [2]:
# ============================================================
# PART 7: EVIDENTLY DRIFT CHECK + AUTO-RETRAIN
# ============================================================

!mkdir -p cloud_functions/drift_check

drift_check_main = '''
import functions_framework
import pandas as pd
import requests
from google.cloud import storage, bigquery
from evidently import Report
from evidently.presets import DataDriftPreset

@functions_framework.http
def check_drift(request):
    """Check for drift and trigger retrain if detected."""
    
    # Load reference data
    client = storage.Client()
    bucket = client.bucket("clv-prediction-data")
    bucket.blob("features/clv_features.parquet").download_to_filename("/tmp/reference.parquet")
    reference = pd.read_parquet("/tmp/reference.parquet")
    
    # Load recent predictions from BigQuery
    bq_client = bigquery.Client()
    query = """
        SELECT recency, frequency, monetary, prediction
        FROM `clv-predictions-mlops.retail_data.prediction_logs`
        WHERE timestamp > TIMESTAMP_SUB(CURRENT_TIMESTAMP(), INTERVAL 7 DAY)
    """
    current = bq_client.query(query).to_dataframe()
    
    if len(current) < 10:
        return {"status": "skipped", "reason": "Not enough data", "rows": len(current)}
    
    # Run Evidently drift check
    ref_subset = reference[["recency_days", "frequency", "monetary"]].rename(columns={"recency_days": "recency"})
    cur_subset = current[["recency", "frequency", "monetary"]]
    
    drift_report = Report([DataDriftPreset()])
    result = drift_report.run(reference_data=ref_subset, current_data=cur_subset)
    
    drift_detected = result.dict()["metrics"][0]["result"]["dataset_drift"]
    
    if drift_detected:
        # Call the retrain function
        retrain_url = "https://clv-retrain-trigger-cpvl5opmca-uc.a.run.app"
        response = requests.post(retrain_url)
        return {"status": "drift_detected", "retrain_triggered": True, "retrain_response": response.status_code}
    
    return {"status": "no_drift", "retrain_triggered": False}
'''

with open("cloud_functions/drift_check/main.py", "w") as f:
    f.write(drift_check_main)

drift_check_requirements = '''
functions-framework==3.*
google-cloud-storage>=2.10.0
google-cloud-bigquery>=3.11.0
pandas>=2.0.0
pyarrow>=12.0.0
evidently>=0.4.0
requests>=2.31.0
'''

with open("cloud_functions/drift_check/requirements.txt", "w") as f:
    f.write(drift_check_requirements.strip())

print("Created cloud_functions/drift_check/")
print("  - main.py")
print("  - requirements.txt")

Created cloud_functions/drift_check/
  - main.py
  - requirements.txt


In [5]:
# Deploy drift check function
!gcloud functions deploy clv-drift-check \
    --gen2 \
    --runtime=python310 \
    --region={REGION} \
    --source=cloud_functions/drift_check \
    --entry-point=check_drift \
    --trigger-http \
    --allow-unauthenticated \
    --memory=1Gi \
    --timeout=300 \
    --project={PROJECT_ID}

print("Drift check function deployed!")

Preparing function...done.                                                     
Deploying function...                                                          
  . [Build]                                                                    
  . [Service]                                                                  
  . [ArtifactRegistry]                                                         
  . [Healthcheck]                                                              
  . [Triggercheck]                                                             
  Deploying function...                                                        





⠛ Deploying function...                                                        
  ⠛ [Build]                                                                    




⠹ Deploying function...                                                        
  ⠹ [Build] Build in progress... Logs are available at [https://console.cloud.g
  oogle.com/cloud-build/builds;

In [7]:
# Update requirements with sniffio
drift_check_requirements = '''
functions-framework==3.*
google-cloud-storage>=2.10.0
google-cloud-bigquery>=3.11.0
pandas>=2.0.0
pyarrow>=12.0.0
evidently>=0.4.0
requests>=2.31.0
sniffio>=1.3.0
anyio>=4.0.0
'''

with open("cloud_functions/drift_check/requirements.txt", "w") as f:
    f.write(drift_check_requirements.strip())

# Redeploy
!gcloud functions deploy clv-drift-check \
    --gen2 \
    --runtime=python310 \
    --region={REGION} \
    --source=cloud_functions/drift_check \
    --entry-point=check_drift \
    --trigger-http \
    --allow-unauthenticated \
    --memory=1Gi \
    --timeout=300 \
    --project={PROJECT_ID}

print("Drift check function redeployed!")

Preparing function...done.                                                     
Updating function (may take a while)...                                        
  . [Build]                                                                    
  . [Service]                                                                  
  . [ArtifactRegistry]                                                         
  . [Healthcheck]                                                              
  . [Triggercheck]                                                             
  Updating function (may take a while)...                                      





⠛ Updating function (may take a while)...                                      
  ⠛ [Build]                                                                    




⠹ Updating function (may take a while)...                                      
  ⠹ [Build] Build in progress... Logs are available at [https://console.cloud.g
  oogle.com/cloud-build/builds;

In [9]:
# Get drift check function URL
!gcloud functions describe clv-drift-check --region={REGION} --project={PROJECT_ID} --format='value(serviceConfig.uri)'

# Create Cloud Scheduler to call drift check weekly
!gcloud scheduler jobs create http clv-weekly-drift-check \
    --location={REGION} \
    --schedule="0 9 * * 1" \
    --uri="https://clv-drift-check-cpvl5opmca-uc.a.run.app" \
    --http-method=POST \
    --project={PROJECT_ID}

print("Cloud Scheduler created - runs every Monday 9am")

^C


Command killed by keyboard interrupt

^C


Command killed by keyboard interrupt

Cloud Scheduler created - runs every Monday 9am


In [11]:
# Update Streamlit app with fixed architecture diagram
app_code = '''
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import tensorflow as tf
import joblib
from google.cloud import storage, bigquery
from datetime import datetime
import os

st.set_page_config(page_title="CLV Prediction MLOps", layout="wide")

# Initialize BigQuery client for logging
@st.cache_resource
def get_bq_client():
    try:
        return bigquery.Client(project="clv-predictions-mlops")
    except:
        return None

bq_client = get_bq_client()

def log_prediction(features_dict, prediction):
    """Log prediction to BigQuery for monitoring"""
    if bq_client is None:
        return
    try:
        table_id = "clv-predictions-mlops.retail_data.prediction_logs"
        row = {
            "timestamp": datetime.utcnow().isoformat(),
            "recency": features_dict.get("recency", 0),
            "frequency": features_dict.get("frequency", 0),
            "monetary": features_dict.get("monetary", 0),
            "prediction": float(prediction)
        }
        errors = bq_client.insert_rows_json(table_id, [row])
    except Exception as e:
        pass

# Load model, scaler, and baseline features from GCS
@st.cache_resource
def load_artifacts():
    try:
        client = storage.Client()
        bucket = client.bucket("clv-prediction-data")
        
        # Download model
        bucket.blob("models/clv_model_tuned.keras").download_to_filename("/tmp/model.keras")
        model = tf.keras.models.load_model("/tmp/model.keras")
        
        # Download scaler
        bucket.blob("models/clv_scaler.pkl").download_to_filename("/tmp/scaler.pkl")
        scaler = joblib.load("/tmp/scaler.pkl")
        
        # Download feature data for baseline
        bucket.blob("features/clv_features.parquet").download_to_filename("/tmp/features.parquet")
        df = pd.read_parquet("/tmp/features.parquet")
        feature_cols = [c for c in df.columns if c not in ["customer_id", "target_clv"]]
        baseline = df[feature_cols].median().values
        
        return model, scaler, baseline, feature_cols
    except Exception as e:
        st.error(f"Could not load model: {e}")
        return None, None, None, None

model, scaler, baseline_features, feature_cols = load_artifacts()

# Sidebar
st.sidebar.header("Model Info")
st.sidebar.metric("Model Type", "Hybrid NN")
st.sidebar.metric("Best MAE", "$1,449")
st.sidebar.metric("Improvement", "27%")

st.sidebar.markdown("---")
st.sidebar.markdown("### Features")
st.sidebar.markdown("""
- 12 numerical features (RFM+)
- 384 text embeddings (Hugging Face)
- Tuned via Vertex AI Vizier
""")

# Main content
st.title("Customer Lifetime Value Prediction")
st.markdown("**MLOps Pipeline Demo** - Hybrid Neural Network with Hugging Face Embeddings")

tab1, tab2, tab3, tab4 = st.tabs(["Predict CLV", "Model Performance", "Feature Importance", "Architecture"])

with tab1:
    st.header("Predict Customer Lifetime Value")
    
    col1, col2 = st.columns(2)
    
    with col1:
        st.subheader("Customer Features")
        
        recency = st.slider("Recency (days since last purchase)", 0, 365, 30)
        frequency = st.slider("Frequency (number of orders)", 1, 50, 5)
        monetary = st.number_input("Monetary (total spend $)", 0, 50000, 500)
        avg_order = st.number_input("Average Order Value $", 0, 5000, 100)
        tenure = st.slider("Customer Tenure (days)", 0, 365, 180)
        unique_products = st.slider("Unique Products Purchased", 1, 100, 10)
    
    with col2:
        st.subheader("Prediction")
        
        if st.button("Predict CLV", type="primary"):
            if model is not None and baseline_features is not None:
                # Start with median customer baseline (includes real embeddings)
                features = baseline_features.copy()
                
                # Override with slider values
                if "recency_days" in feature_cols:
                    features[feature_cols.index("recency_days")] = recency
                if "frequency" in feature_cols:
                    features[feature_cols.index("frequency")] = frequency
                if "monetary" in feature_cols:
                    features[feature_cols.index("monetary")] = monetary
                if "avg_order_value" in feature_cols:
                    features[feature_cols.index("avg_order_value")] = avg_order
                if "customer_tenure_days" in feature_cols:
                    features[feature_cols.index("customer_tenure_days")] = tenure
                if "unique_products" in feature_cols:
                    features[feature_cols.index("unique_products")] = unique_products
                
                # Scale and predict with ACTUAL model
                features_scaled = scaler.transform(features.reshape(1, -1))
                prediction = model.predict(features_scaled, verbose=0)[0][0]
                prediction = max(0, prediction)
                
                # Log to BigQuery
                log_prediction({
                    "recency": recency,
                    "frequency": frequency,
                    "monetary": monetary
                }, prediction)
                
                st.metric("Predicted 12-Month CLV", f"${prediction:,.0f}")
                
                # Customer segment
                if prediction > 5000:
                    st.success("🌟 High-Value Customer")
                elif prediction > 1000:
                    st.info("📈 Medium-Value Customer")
                else:
                    st.warning("📊 Low-Value Customer")
            else:
                st.error("Model not loaded")

with tab2:
    st.header("Model Performance")
    
    col1, col2 = st.columns(2)
    
    with col1:
        # Tuning results
        tuning_data = {
            "Model": ["Baseline", "Tuned"],
            "MAE ($)": [1987, 1449]
        }
        fig = px.bar(tuning_data, x="Model", y="MAE ($)", 
                     title="Hyperparameter Tuning Impact",
                     color="Model", color_discrete_map={"Baseline": "gray", "Tuned": "green"})
        st.plotly_chart(fig, use_container_width=True)
    
    with col2:
        # Metrics comparison
        st.markdown("### Performance Metrics")
        st.markdown("""
        | Metric | Baseline | Tuned | Improvement |
        |--------|----------|-------|-------------|
        | MAE | $1,987 | $1,449 | **27%** |
        | R² | 0.104 | 0.15+ | **~50%** |
        """)
        
        st.markdown("### Vizier Tuning")
        st.markdown("""
        - **Trials**: 15
        - **Algorithm**: Random Search
        - **Best params**: 201/74 units, 0.25 dropout, 0.0027 lr
        """)

with tab3:
    st.header("Feature Importance (Integrated Gradients)")
    
    importance_data = {
        "Feature": ["monetary", "unique_purchase_days", "frequency", "orders_per_month", 
                   "total_items_purchased", "unique_products", "avg_order_value", 
                   "customer_tenure_days", "emb_115", "emb_279"],
        "Attribution": [1900, 1350, 1300, 1150, 1100, 1000, 250, 220, 150, 140]
    }
    
    fig = px.bar(importance_data, x="Attribution", y="Feature", orientation="h",
                 title="Top Features Driving CLV Predictions",
                 color="Attribution", color_continuous_scale="greens")
    fig.update_layout(yaxis={"categoryorder": "total ascending"})
    st.plotly_chart(fig, use_container_width=True)
    
    st.markdown("""
    **Key Insights:**
    - **Monetary** (past spend) is the strongest predictor
    - **Engagement metrics** (purchase frequency, unique days) rank highly
    - **Text embeddings** (emb_*) contribute - what customers buy matters
    """)

with tab4:
    st.header("MLOps Architecture")
    
    st.code("""
                              CLV PREDICTION MLOPS PIPELINE

    ═══════════════════════════════════════════════════════════════════════════
                                   DATA LAYER
    ═══════════════════════════════════════════════════════════════════════════
    
      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐
      │   BigQuery  │─────▶│   Dataproc  │─────▶│  Hugging    │─────▶│     GCS     │
      │  (Raw Data) │      │  (PySpark)  │      │    Face     │      │  (Features) │
      └─────────────┘      └─────────────┘      └─────────────┘      └──────┬──────┘
                                                                            │
                                                                            ▼
    ═══════════════════════════════════════════════════════════════════════════
                                    ML LAYER
    ═══════════════════════════════════════════════════════════════════════════
    
      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐
      │   Vertex    │─────▶│   Vertex    │─────▶│    Model    │─────▶│  Cloud Run  │
      │   Vizier    │      │  Pipeline   │      │  Registry   │      │   (Demo)    │
      └─────────────┘      └─────────────┘      └──────┬──────┘      └──────┬──────┘
                                  ▲                    │                    │
                                  │                    │                    │
                                  │ Retrain            │                    ▼
    ═══════════════════════════════════════════════════════════════════════════
                               MONITORING LAYER
    ═══════════════════════════════════════════════════════════════════════════
                                  │                    │
      ┌─────────────┐      ┌──────┴──────┐      ┌──────▼──────┐      ┌─────────────┐
      │    Cloud    │─────▶│  Evidently  │─────▶│    Cloud    │      │   BigQuery  │
      │  Scheduler  │      │   (Drift)   │      │  Function   │◀─────│   (Logs)    │
      └─────────────┘      └─────────────┘      └─────────────┘      └─────────────┘
    
    """, language=None)
    
    col1, col2, col3 = st.columns(3)
    
    with col1:
        st.markdown("**Data Layer**")
        st.markdown("- BigQuery (storage)")
        st.markdown("- PySpark (processing)")
        st.markdown("- Hugging Face (embeddings)")
    
    with col2:
        st.markdown("**ML Layer**")
        st.markdown("- Hybrid NN (TensorFlow)")
        st.markdown("- Vizier (tuning)")
        st.markdown("- Vertex Pipelines")
    
    with col3:
        st.markdown("**Monitoring**")
        st.markdown("- BigQuery (logs)")
        st.markdown("- Evidently AI (drift)")
        st.markdown("- Cloud Functions (retrain)")

# Footer
st.markdown("---")
st.caption("📝 Note: This demo exposes 6 of 396 features. The model uses median customer values as baseline (including 384 Hugging Face text embeddings) and overrides with slider inputs for real-time prediction.")
st.markdown("**Project by Arion Farhi** | [GitHub](https://github.com/arion-farhi)")
'''

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Updated streamlit_app/app.py with fixed architecture diagram")

Updated streamlit_app/app.py with fixed architecture diagram


In [14]:
# Update Streamlit app with GKE in architecture diagram and tech stack
app_code = open("streamlit_app/app.py").read()

old_diagram = '''    st.code("""
                              CLV PREDICTION MLOPS PIPELINE

    ═══════════════════════════════════════════════════════════════════════════
                                   DATA LAYER
    ═══════════════════════════════════════════════════════════════════════════
    
      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐
      │   BigQuery  │─────▶│   Dataproc  │─────▶│  Hugging    │─────▶│     GCS     │
      │  (Raw Data) │      │  (PySpark)  │      │    Face     │      │  (Features) │
      └─────────────┘      └─────────────┘      └─────────────┘      └──────┬──────┘
                                                                            │
                                                                            ▼
    ═══════════════════════════════════════════════════════════════════════════
                                    ML LAYER
    ═══════════════════════════════════════════════════════════════════════════
    
      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐
      │   Vertex    │─────▶│   Vertex    │─────▶│    Model    │─────▶│  Cloud Run  │
      │   Vizier    │      │  Pipeline   │      │  Registry   │      │   (Demo)    │
      └─────────────┘      └─────────────┘      └──────┬──────┘      └──────┬──────┘
                                  ▲                    │                    │
                                  │                    │                    │
                                  │ Retrain            │                    ▼
    ═══════════════════════════════════════════════════════════════════════════
                               MONITORING LAYER
    ═══════════════════════════════════════════════════════════════════════════
                                  │                    │
      ┌─────────────┐      ┌──────┴──────┐      ┌──────▼──────┐      ┌─────────────┐
      │    Cloud    │─────▶│  Evidently  │─────▶│    Cloud    │      │   BigQuery  │
      │  Scheduler  │      │   (Drift)   │      │  Function   │◀─────│   (Logs)    │
      └─────────────┘      └─────────────┘      └─────────────┘      └─────────────┘
    
    """, language=None)
    
    col1, col2, col3 = st.columns(3)
    
    with col1:
        st.markdown("**Data Layer**")
        st.markdown("- BigQuery (storage)")
        st.markdown("- PySpark (processing)")
        st.markdown("- Hugging Face (embeddings)")
    
    with col2:
        st.markdown("**ML Layer**")
        st.markdown("- Hybrid NN (TensorFlow)")
        st.markdown("- Vizier (tuning)")
        st.markdown("- Vertex Pipelines")
    
    with col3:
        st.markdown("**Monitoring**")
        st.markdown("- BigQuery (logs)")
        st.markdown("- Evidently AI (drift)")
        st.markdown("- Cloud Functions (retrain)")'''

new_diagram = '''    st.code("""
                              CLV PREDICTION MLOPS PIPELINE

    ═══════════════════════════════════════════════════════════════════════════
                                   DATA LAYER
    ═══════════════════════════════════════════════════════════════════════════
    
      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐
      │   BigQuery  │─────▶│   Dataproc  │─────▶│  Hugging    │─────▶│     GCS     │
      │  (Raw Data) │      │  (PySpark)  │      │    Face     │      │  (Features) │
      └─────────────┘      └─────────────┘      └─────────────┘      └──────┬──────┘
                                                                            │
                                                                            ▼
    ═══════════════════════════════════════════════════════════════════════════
                                    ML LAYER
    ═══════════════════════════════════════════════════════════════════════════
    
      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐      ┌─────────────┐
      │   Vertex    │─────▶│   Vertex    │─────▶│    Model    │─────▶│     GKE     │
      │   Vizier    │      │  Pipeline   │      │  Registry   │      │ (Production)│
      └─────────────┘      └─────────────┘      └──────┬──────┘      └─────────────┘
                                  ▲                    │                    
                                  │                    ├───────────▶┌─────────────┐
                                  │ Retrain            │            │  Cloud Run  │
                                  │                    │            │(Demo + A/B) │
    ═══════════════════════════════════════════════════════════════════════════
                               MONITORING LAYER        │            └──────┬──────┘
    ═══════════════════════════════════════════════════════════════════════════
                                  │                    │                   │
      ┌─────────────┐      ┌──────┴──────┐      ┌──────▼──────┐      ┌──────▼──────┐
      │    Cloud    │─────▶│  Evidently  │─────▶│    Cloud    │      │   BigQuery  │
      │  Scheduler  │      │   (Drift)   │      │  Function   │      │   (Logs)    │
      └─────────────┘      └─────────────┘      └─────────────┘      └─────────────┘
    
    """, language=None)
    
    col1, col2, col3 = st.columns(3)
    
    with col1:
        st.markdown("**Data Layer**")
        st.markdown("- BigQuery (storage)")
        st.markdown("- PySpark (processing)")
        st.markdown("- Hugging Face (embeddings)")
    
    with col2:
        st.markdown("**Deployment**")
        st.markdown("- GKE (production)")
        st.markdown("- Cloud Run (demo + A/B)")
        st.markdown("- Model Registry")
    
    with col3:
        st.markdown("**Monitoring**")
        st.markdown("- BigQuery (logs)")
        st.markdown("- Evidently AI (drift)")
        st.markdown("- Cloud Scheduler")
        st.markdown("- Cloud Functions (retrain)")'''

app_code = app_code.replace(old_diagram, new_diagram)

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Updated diagram with GKE and tech stack")

Updated diagram with GKE and tech stack


In [15]:
!gcloud builds submit streamlit_app \
    --tag gcr.io/{PROJECT_ID}/clv-demo \
    --project={PROJECT_ID}

!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --platform managed \
    --region {REGION} \
    --allow-unauthenticated \
    --memory 2Gi \
    --project={PROJECT_ID}

Creating temporary archive of 3 file(s) totalling 13.1 KiB before compression.
Uploading tarball of [streamlit_app] to [gs://clv-predictions-mlops_cloudbuild/source/1765504062.832507-0581e1c10d904b33adc3e617f901a09f.tgz]
Created [https://cloudbuild.googleapis.com/v1/projects/clv-predictions-mlops/locations/global/builds/f583bde2-45a2-44e6-a45e-c97dd303ed20].
Logs are available at [ https://console.cloud.google.com/cloud-build/builds/f583bde2-45a2-44e6-a45e-c97dd303ed20?project=674754622820 ].
Waiting for build to complete. Polling interval: 1 second(s).
----------------------------- REMOTE BUILD OUTPUT ------------------------------
starting build "f583bde2-45a2-44e6-a45e-c97dd303ed20"

FETCHSOURCE
Fetching storage object: gs://clv-predictions-mlops_cloudbuild/source/1765504062.832507-0581e1c10d904b33adc3e617f901a09f.tgz#1765504063009494
Copying gs://clv-predictions-mlops_cloudbuild/source/1765504062.832507-0581e1c10d904b33adc3e617f901a09f.tgz#1765504063009494...
/ [1 files][  3.8 KiB/

In [19]:
# Complete rewrite of app.py with all fixes
app_code = '''
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import tensorflow as tf
import joblib
from google.cloud import storage, bigquery
from datetime import datetime
import os

st.set_page_config(page_title="CLV Prediction MLOps", layout="wide")

# Initialize BigQuery client for logging
@st.cache_resource
def get_bq_client():
    try:
        return bigquery.Client(project="clv-predictions-mlops")
    except:
        return None

bq_client = get_bq_client()

def log_prediction(features_dict, prediction):
    """Log prediction to BigQuery for monitoring"""
    if bq_client is None:
        return
    try:
        table_id = "clv-predictions-mlops.retail_data.prediction_logs"
        row = {
            "timestamp": datetime.utcnow().isoformat(),
            "recency": features_dict.get("recency", 0),
            "frequency": features_dict.get("frequency", 0),
            "monetary": features_dict.get("monetary", 0),
            "prediction": float(prediction)
        }
        errors = bq_client.insert_rows_json(table_id, [row])
    except Exception as e:
        pass

# Load model, scaler, and baseline features from GCS
@st.cache_resource
def load_artifacts():
    try:
        client = storage.Client()
        bucket = client.bucket("clv-prediction-data")
        
        # Download model
        bucket.blob("models/clv_model_tuned.keras").download_to_filename("/tmp/model.keras")
        model = tf.keras.models.load_model("/tmp/model.keras")
        
        # Download scaler
        bucket.blob("models/clv_scaler.pkl").download_to_filename("/tmp/scaler.pkl")
        scaler = joblib.load("/tmp/scaler.pkl")
        
        # Download feature data for baseline
        bucket.blob("features/clv_features.parquet").download_to_filename("/tmp/features.parquet")
        df = pd.read_parquet("/tmp/features.parquet")
        feature_cols = [c for c in df.columns if c not in ["customer_id", "target_clv"]]
        baseline = df[feature_cols].median().values
        
        return model, scaler, baseline, feature_cols
    except Exception as e:
        st.error(f"Could not load model: {e}")
        return None, None, None, None

model, scaler, baseline_features, feature_cols = load_artifacts()

# Sidebar
st.sidebar.header("Model Info")
st.sidebar.metric("Model Type", "Hybrid NN")
st.sidebar.metric("Median AE", "$429")
st.sidebar.metric("R²", "0.735")

st.sidebar.markdown("---")
st.sidebar.markdown("### Features")
st.sidebar.markdown("""
- 12 numerical features (RFM+)
- 384 text embeddings (Hugging Face)
- Tuned via Vertex AI Vizier
""")

# Main content
st.title("Customer Lifetime Value Prediction")
st.markdown("**MLOps Pipeline Demo** - Hybrid Neural Network with Hugging Face Embeddings")

tab1, tab2, tab3, tab4 = st.tabs(["Predict CLV", "Model Performance", "Feature Importance", "Architecture"])

with tab1:
    st.header("Predict Customer Lifetime Value")
    
    col1, col2 = st.columns(2)
    
    with col1:
        st.subheader("Customer Features")
        
        recency = st.slider("Recency (days since last purchase)", 0, 365, 30)
        frequency = st.slider("Frequency (number of orders)", 1, 50, 5)
        monetary = st.number_input("Monetary (total spend $)", 0, 50000, 500)
        avg_order = st.number_input("Average Order Value $", 0, 5000, 100)
        tenure = st.slider("Customer Tenure (days)", 0, 365, 180)
        unique_products = st.slider("Unique Products Purchased", 1, 100, 10)
    
    with col2:
        st.subheader("Prediction")
        
        if st.button("Predict CLV", type="primary"):
            if model is not None and baseline_features is not None:
                # Start with median customer baseline (includes real embeddings)
                features = baseline_features.copy()
                
                # Override with slider values
                if "recency_days" in feature_cols:
                    features[feature_cols.index("recency_days")] = recency
                if "frequency" in feature_cols:
                    features[feature_cols.index("frequency")] = frequency
                if "monetary" in feature_cols:
                    features[feature_cols.index("monetary")] = monetary
                if "avg_order_value" in feature_cols:
                    features[feature_cols.index("avg_order_value")] = avg_order
                if "customer_tenure_days" in feature_cols:
                    features[feature_cols.index("customer_tenure_days")] = tenure
                if "unique_products" in feature_cols:
                    features[feature_cols.index("unique_products")] = unique_products
                
                # Scale and predict with ACTUAL model
                features_scaled = scaler.transform(features.reshape(1, -1))
                prediction = model.predict(features_scaled, verbose=0)[0][0]
                prediction = max(0, prediction)
                
                # Log to BigQuery
                log_prediction({
                    "recency": recency,
                    "frequency": frequency,
                    "monetary": monetary
                }, prediction)
                
                st.metric("Predicted 12-Month CLV", f"${prediction:,.0f}")
                
                # Customer segment
                if prediction > 5000:
                    st.success("🌟 High-Value Customer")
                elif prediction > 1000:
                    st.info("📈 Medium-Value Customer")
                else:
                    st.warning("📊 Low-Value Customer")
            else:
                st.error("Model not loaded")

with tab2:
    st.header("Model Performance")
    
    col1, col2 = st.columns(2)
    
    with col1:
        # Tuning results
        tuning_data = {
            "Metric": ["Median AE", "R²", "Within $1K"],
            "Value": [429, 73.5, 68.6]
        }
        fig = px.bar(tuning_data, x="Metric", y="Value", 
                     title="Model Performance Metrics",
                     color="Metric", color_discrete_sequence=["#2ecc71", "#3498db", "#9b59b6"])
        st.plotly_chart(fig, use_container_width=True)
    
    with col2:
        st.markdown("### Performance Metrics")
        st.markdown("""
        | Metric | Value |
        |--------|-------|
        | Median Absolute Error | $429 |
        | R² Score | 0.735 |
        | Predictions within $1,000 | 68.6% |
        """)
        
        st.markdown("### Vizier Tuning")
        st.markdown("""
        - **Trials**: 15
        - **Algorithm**: Random Search
        - **Best params**: 201/74 units, 0.25 dropout, 0.0027 lr
        """)

with tab3:
    st.header("Feature Importance (Integrated Gradients)")
    
    importance_data = {
        "Feature": ["monetary", "unique_purchase_days", "frequency", "orders_per_month", 
                   "total_items_purchased", "unique_products", "avg_order_value", 
                   "customer_tenure_days", "emb_115", "emb_279"],
        "Attribution": [1900, 1350, 1300, 1150, 1100, 1000, 250, 220, 150, 140]
    }
    
    fig = px.bar(importance_data, x="Attribution", y="Feature", orientation="h",
                 title="Top Features Driving CLV Predictions",
                 color="Attribution", color_continuous_scale="greens")
    fig.update_layout(yaxis={"categoryorder": "total ascending"})
    st.plotly_chart(fig, use_container_width=True)
    
    st.markdown("""
    **Key Insights:**
    - **Monetary** (past spend) is the strongest predictor
    - **Engagement metrics** (purchase frequency, unique days) rank highly
    - **Text embeddings** (emb_*) contribute - what customers buy matters
    """)

with tab4:
    st.header("MLOps Architecture")
    
    st.code("""
                              CLV PREDICTION MLOPS PIPELINE

    ┌─────────────────────────────────────────────────────────────────────────────┐
    │                               DATA LAYER                                    │
    │                                                                             │
    │   ┌──────────┐      ┌──────────┐      ┌──────────┐      ┌──────────┐       │
    │   │ BigQuery │─────▶│ Dataproc │─────▶│ Hugging  │─────▶│   GCS    │       │
    │   │(Raw Data)│      │(PySpark) │      │   Face   │      │(Features)│       │
    │   └──────────┘      └──────────┘      └──────────┘      └────┬─────┘       │
    └─────────────────────────────────────────────────────────────────────────────┘
                                                                   │
                                                                   ▼
    ┌─────────────────────────────────────────────────────────────────────────────┐
    │                                ML LAYER                                     │
    │                                                                             │
    │   ┌──────────┐      ┌──────────┐      ┌──────────┐      ┌──────────┐       │
    │   │  Vertex  │─────▶│  Vertex  │─────▶│  Model   │─────▶│   GKE    │       │
    │   │  Vizier  │      │ Pipeline │      │ Registry │      │  (Prod)  │       │
    │   └──────────┘      └──────────┘      └────┬─────┘      └──────────┘       │
    │                           ▲                │                               │
    │                           │                ├───────────▶┌──────────┐       │
    │                           │                │            │Cloud Run │       │
    │                           │                │            │(Demo+A/B)│       │
    └───────────────────────────│────────────────│────────────└────┬─────┘───────┘
                                │                │                 │
                                │ Retrain        │                 │
                                │                ▼                 ▼
    ┌───────────────────────────│─────────────────────────────────────────────────┐
    │                           │      MONITORING LAYER                           │
    │                           │                                                 │
    │   ┌──────────┐      ┌─────┴────┐      ┌──────────┐      ┌──────────┐       │
    │   │  Cloud   │─────▶│ Evidently│─────▶│  Cloud   │      │ BigQuery │       │
    │   │Scheduler │      │  (Drift) │      │ Function │◀─────│ (Logs)   │       │
    │   └──────────┘      └──────────┘      └──────────┘      └──────────┘       │
    │                                                                             │
    └─────────────────────────────────────────────────────────────────────────────┘
    
    """, language=None)
    
    col1, col2, col3 = st.columns(3)
    
    with col1:
        st.markdown("**Data Layer**")
        st.markdown("- BigQuery (storage)")
        st.markdown("- PySpark (processing)")
        st.markdown("- Hugging Face (embeddings)")
    
    with col2:
        st.markdown("**Deployment**")
        st.markdown("- GKE (production)")
        st.markdown("- Cloud Run (demo + A/B)")
        st.markdown("- Model Registry")
    
    with col3:
        st.markdown("**Monitoring**")
        st.markdown("- Cloud Scheduler")
        st.markdown("- Evidently AI (drift)")
        st.markdown("- Cloud Functions (retrain)")
        st.markdown("- BigQuery (logs)")

# Footer
st.markdown("---")
st.caption("📝 Note: This demo exposes 6 of 396 features. The model uses median customer values as baseline (including 384 Hugging Face text embeddings) and overrides with slider inputs for real-time prediction.")
st.markdown("**Project by Arion Farhi** | [GitHub](https://github.com/arion-farhi)")
'''

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Complete rewrite done with:")
print("  - Median AE $429, R² 0.735, Within $1K 68.6%")
print("  - GKE in diagram")
print("  - Cloud Scheduler in diagram")
print("  - Updated tech stack text")

Complete rewrite done with:
  - Median AE $429, R² 0.735, Within $1K 68.6%
  - GKE in diagram
  - Cloud Scheduler in diagram
  - Updated tech stack text


In [20]:
!gcloud builds submit streamlit_app \
    --tag gcr.io/{PROJECT_ID}/clv-demo \
    --project={PROJECT_ID}

!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --platform managed \
    --region {REGION} \
    --allow-unauthenticated \
    --memory 2Gi \
    --project={PROJECT_ID}

Creating temporary archive of 3 file(s) totalling 13.6 KiB before compression.
Uploading tarball of [streamlit_app] to [gs://clv-predictions-mlops_cloudbuild/source/1765505169.469104-ee68e05511674ef48c952ff7f249b5d6.tgz]
Created [https://cloudbuild.googleapis.com/v1/projects/clv-predictions-mlops/locations/global/builds/f26aa863-c0de-4a81-a39b-4beb3e498d81].
Logs are available at [ https://console.cloud.google.com/cloud-build/builds/f26aa863-c0de-4a81-a39b-4beb3e498d81?project=674754622820 ].
Waiting for build to complete. Polling interval: 1 second(s).
----------------------------- REMOTE BUILD OUTPUT ------------------------------
starting build "f26aa863-c0de-4a81-a39b-4beb3e498d81"

FETCHSOURCE
Fetching storage object: gs://clv-predictions-mlops_cloudbuild/source/1765505169.469104-ee68e05511674ef48c952ff7f249b5d6.tgz#1765505169638917
Copying gs://clv-predictions-mlops_cloudbuild/source/1765505169.469104-ee68e05511674ef48c952ff7f249b5d6.tgz#1765505169638917...
/ [1 files][  3.8 KiB/

In [21]:
# Route all traffic to latest revision
!gcloud run services update-traffic clv-demo \
    --region={REGION} \
    --to-latest \
    --project={PROJECT_ID}

Updating traffic...                                                            
  . Routing traffic...                                                         
  Updating traffic...                                                          

⠛ Updating traffic...                                                          

⠹ Updating traffic...                                                          

⠼ Updating traffic...                                                          
  ⠼ Routing traffic...                                                         
⠶ Updating traffic...                                                          
  ⠶ Routing traffic...                                                         
⠧ Updating traffic...                                                          
  ⠧ Routing traffic...                                                         
⠏ Updating traffic...                                                          
  ⠏ Routing traffic...               

In [22]:
# Complete rewrite with fixes
app_code = '''
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import tensorflow as tf
import joblib
from google.cloud import storage, bigquery
from datetime import datetime
import os

st.set_page_config(page_title="CLV Prediction MLOps", layout="wide")

# Initialize BigQuery client for logging
@st.cache_resource
def get_bq_client():
    try:
        return bigquery.Client(project="clv-predictions-mlops")
    except:
        return None

bq_client = get_bq_client()

def log_prediction(features_dict, prediction):
    """Log prediction to BigQuery for monitoring"""
    if bq_client is None:
        return
    try:
        table_id = "clv-predictions-mlops.retail_data.prediction_logs"
        row = {
            "timestamp": datetime.utcnow().isoformat(),
            "recency": features_dict.get("recency", 0),
            "frequency": features_dict.get("frequency", 0),
            "monetary": features_dict.get("monetary", 0),
            "prediction": float(prediction)
        }
        errors = bq_client.insert_rows_json(table_id, [row])
    except Exception as e:
        pass

# Load model, scaler, and baseline features from GCS
@st.cache_resource
def load_artifacts():
    try:
        client = storage.Client()
        bucket = client.bucket("clv-prediction-data")
        
        # Download model
        bucket.blob("models/clv_model_tuned.keras").download_to_filename("/tmp/model.keras")
        model = tf.keras.models.load_model("/tmp/model.keras")
        
        # Download scaler
        bucket.blob("models/clv_scaler.pkl").download_to_filename("/tmp/scaler.pkl")
        scaler = joblib.load("/tmp/scaler.pkl")
        
        # Download feature data for baseline
        bucket.blob("features/clv_features.parquet").download_to_filename("/tmp/features.parquet")
        df = pd.read_parquet("/tmp/features.parquet")
        feature_cols = [c for c in df.columns if c not in ["customer_id", "target_clv"]]
        baseline = df[feature_cols].median().values
        
        return model, scaler, baseline, feature_cols
    except Exception as e:
        st.error(f"Could not load model: {e}")
        return None, None, None, None

model, scaler, baseline_features, feature_cols = load_artifacts()

# Sidebar
st.sidebar.header("Model Info")
st.sidebar.metric("Model Type", "Hybrid NN")
st.sidebar.metric("Median AE", "$429")
st.sidebar.metric("R²", "0.735")

st.sidebar.markdown("---")
st.sidebar.markdown("### Features")
st.sidebar.markdown("""
- 12 numerical features (RFM+)
- 384 text embeddings (Hugging Face)
- Tuned via Vertex AI Vizier
""")

# Main content
st.title("Customer Lifetime Value Prediction")
st.markdown("**MLOps Pipeline Demo** - Hybrid Neural Network with Hugging Face Embeddings")

tab1, tab2, tab3, tab4 = st.tabs(["Predict CLV", "Model Performance", "Feature Importance", "Architecture"])

with tab1:
    st.header("Predict Customer Lifetime Value")
    
    col1, col2 = st.columns(2)
    
    with col1:
        st.subheader("Customer Features")
        
        recency = st.slider("Recency (days since last purchase)", 0, 365, 30)
        frequency = st.slider("Frequency (number of orders)", 1, 50, 5)
        avg_order = st.number_input("Average Order Value $", 0, 5000, 100)
        tenure = st.slider("Customer Tenure (days)", 0, 365, 180)
        unique_products = st.slider("Unique Products Purchased", 1, 100, 10)
        
        # Calculate monetary from frequency * avg_order
        monetary = frequency * avg_order
        st.caption(f"Calculated Monetary (Frequency × Avg Order): ${monetary:,}")
    
    with col2:
        st.subheader("Prediction")
        
        if st.button("Predict CLV", type="primary"):
            if model is not None and baseline_features is not None:
                # Start with median customer baseline (includes real embeddings)
                features = baseline_features.copy()
                
                # Override with slider values
                if "recency_days" in feature_cols:
                    features[feature_cols.index("recency_days")] = recency
                if "frequency" in feature_cols:
                    features[feature_cols.index("frequency")] = frequency
                if "monetary" in feature_cols:
                    features[feature_cols.index("monetary")] = monetary
                if "avg_order_value" in feature_cols:
                    features[feature_cols.index("avg_order_value")] = avg_order
                if "customer_tenure_days" in feature_cols:
                    features[feature_cols.index("customer_tenure_days")] = tenure
                if "unique_products" in feature_cols:
                    features[feature_cols.index("unique_products")] = unique_products
                
                # Scale and predict with ACTUAL model
                features_scaled = scaler.transform(features.reshape(1, -1))
                prediction = model.predict(features_scaled, verbose=0)[0][0]
                prediction = max(0, prediction)
                
                # Log to BigQuery
                log_prediction({
                    "recency": recency,
                    "frequency": frequency,
                    "monetary": monetary
                }, prediction)
                
                st.metric("Predicted 12-Month CLV", f"${prediction:,.0f}")
                
                # Customer segment
                if prediction > 5000:
                    st.success("🌟 High-Value Customer")
                elif prediction > 1000:
                    st.info("📈 Medium-Value Customer")
                else:
                    st.warning("📊 Low-Value Customer")
            else:
                st.error("Model not loaded")

with tab2:
    st.header("Model Performance")
    
    col1, col2 = st.columns(2)
    
    with col1:
        # Baseline vs Tuned MAE comparison
        tuning_data = {
            "Model": ["Baseline", "Tuned"],
            "MAE ($)": [1987, 1449]
        }
        fig = px.bar(tuning_data, x="Model", y="MAE ($)", 
                     title="Hyperparameter Tuning Impact (27% Improvement)",
                     color="Model", color_discrete_map={"Baseline": "gray", "Tuned": "green"})
        st.plotly_chart(fig, use_container_width=True)
    
    with col2:
        st.markdown("### Performance Metrics")
        st.markdown("""
        | Metric | Value |
        |--------|-------|
        | Median Absolute Error | $429 |
        | R² Score | 0.735 |
        | Predictions within $1,000 | 68.6% |
        """)
        
        st.markdown("### Vizier Tuning")
        st.markdown("""
        - **Trials**: 15
        - **Algorithm**: Random Search
        - **Best params**: 201/74 units, 0.25 dropout, 0.0027 lr
        """)

with tab3:
    st.header("Feature Importance (Integrated Gradients)")
    
    importance_data = {
        "Feature": ["monetary", "unique_purchase_days", "frequency", "orders_per_month", 
                   "total_items_purchased", "unique_products", "avg_order_value", 
                   "customer_tenure_days", "emb_115", "emb_279"],
        "Attribution": [1900, 1350, 1300, 1150, 1100, 1000, 250, 220, 150, 140]
    }
    
    fig = px.bar(importance_data, x="Attribution", y="Feature", orientation="h",
                 title="Top Features Driving CLV Predictions",
                 color="Attribution", color_continuous_scale="greens")
    fig.update_layout(yaxis={"categoryorder": "total ascending"})
    st.plotly_chart(fig, use_container_width=True)
    
    st.markdown("""
    **Key Insights:**
    - **Monetary** (past spend) is the strongest predictor
    - **Engagement metrics** (purchase frequency, unique days) rank highly
    - **Text embeddings** (emb_*) contribute - what customers buy matters
    """)

with tab4:
    st.header("MLOps Architecture")
    
    st.code("""
                            CLV PREDICTION MLOPS PIPELINE

┌──────────────────────────────────────────────────────────────────────────────┐
│                                DATA LAYER                                    │
│                                                                              │
│  ┌───────────┐     ┌───────────┐     ┌───────────┐     ┌───────────┐        │
│  │  BigQuery │────▶│  Dataproc │────▶│  Hugging  │────▶│    GCS    │        │
│  │ (Raw Data)│     │ (PySpark) │     │   Face    │     │(Features) │        │
│  └───────────┘     └───────────┘     └───────────┘     └─────┬─────┘        │
│                                                              │              │
└──────────────────────────────────────────────────────────────│──────────────┘
                                                               │
                                                               ▼
┌──────────────────────────────────────────────────────────────────────────────┐
│                                 ML LAYER                                     │
│                                                                              │
│  ┌───────────┐     ┌───────────┐     ┌───────────┐     ┌───────────┐        │
│  │  Vertex   │────▶│  Vertex   │────▶│   Model   │────▶│    GKE    │        │
│  │  Vizier   │     │ Pipeline  │     │ Registry  │     │  (Prod)   │        │
│  └───────────┘     └─────┬─────┘     └─────┬─────┘     └───────────┘        │
│                          │                 │                                 │
│                          │                 │           ┌───────────┐        │
│                          │                 └──────────▶│ Cloud Run │        │
│                          │                             │(Demo+A/B) │        │
│                          │                             └─────┬─────┘        │
└──────────────────────────│───────────────────────────────────│──────────────┘
                           │                                   │
                           │ Retrain                           │
                           │                                   ▼
┌──────────────────────────│───────────────────────────────────────────────────┐
│                          │       MONITORING LAYER                            │
│                          │                                                   │
│  ┌───────────┐     ┌─────┴─────┐     ┌───────────┐     ┌───────────┐        │
│  │   Cloud   │────▶│ Evidently │────▶│   Cloud   │     │  BigQuery │        │
│  │ Scheduler │     │  (Drift)  │     │ Function  │◀────│  (Logs)   │        │
│  └───────────┘     └───────────┘     └───────────┘     └───────────┘        │
│                                                                              │
└──────────────────────────────────────────────────────────────────────────────┘
    """, language=None)
    
    col1, col2, col3 = st.columns(3)
    
    with col1:
        st.markdown("**Data Layer**")
        st.markdown("- BigQuery (storage)")
        st.markdown("- PySpark (processing)")
        st.markdown("- Hugging Face (embeddings)")
    
    with col2:
        st.markdown("**Deployment**")
        st.markdown("- GKE (production)")
        st.markdown("- Cloud Run (demo + A/B)")
        st.markdown("- Model Registry")
    
    with col3:
        st.markdown("**Monitoring**")
        st.markdown("- Cloud Scheduler")
        st.markdown("- Evidently AI (drift)")
        st.markdown("- Cloud Functions (retrain)")
        st.markdown("- BigQuery (logs)")

# Footer
st.markdown("---")
st.caption("📝 Note: This demo exposes 5 of 396 features. The model uses median customer values as baseline (including 384 Hugging Face text embeddings) and overrides with slider inputs for real-time prediction.")
st.markdown("**Project by Arion Farhi** | [GitHub](https://github.com/arion-farhi)")
'''

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Updated app.py with:")
print("  - Removed monetary input, calculated from frequency * avg_order")
print("  - Added back baseline vs tuned MAE chart")
print("  - Fixed architecture diagram lines")

Updated app.py with:
  - Removed monetary input, calculated from frequency * avg_order
  - Added back baseline vs tuned MAE chart
  - Fixed architecture diagram lines


In [23]:
!gcloud builds submit streamlit_app \
    --tag gcr.io/{PROJECT_ID}/clv-demo \
    --project={PROJECT_ID}

!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --platform managed \
    --region {REGION} \
    --allow-unauthenticated \
    --memory 2Gi \
    --project={PROJECT_ID}

!gcloud run services update-traffic clv-demo \
    --region={REGION} \
    --to-latest \
    --project={PROJECT_ID}

Creating temporary archive of 3 file(s) totalling 13.9 KiB before compression.
Uploading tarball of [streamlit_app] to [gs://clv-predictions-mlops_cloudbuild/source/1765505996.72352-031ace7aa78445308b1c2c3f54a72e2f.tgz]
Created [https://cloudbuild.googleapis.com/v1/projects/clv-predictions-mlops/locations/global/builds/9f36f6e3-591d-483a-9005-1b7446aff72a].
Logs are available at [ https://console.cloud.google.com/cloud-build/builds/9f36f6e3-591d-483a-9005-1b7446aff72a?project=674754622820 ].
Waiting for build to complete. Polling interval: 1 second(s).
----------------------------- REMOTE BUILD OUTPUT ------------------------------
starting build "9f36f6e3-591d-483a-9005-1b7446aff72a"

FETCHSOURCE
Fetching storage object: gs://clv-predictions-mlops_cloudbuild/source/1765505996.72352-031ace7aa78445308b1c2c3f54a72e2f.tgz#1765505996887498
Copying gs://clv-predictions-mlops_cloudbuild/source/1765505996.72352-031ace7aa78445308b1c2c3f54a72e2f.tgz#1765505996887498...
/ [1 files][  3.9 KiB/  3

In [24]:
# Complete rewrite with all fixes
app_code = '''
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import tensorflow as tf
import joblib
from google.cloud import storage, bigquery
from datetime import datetime
import os

st.set_page_config(page_title="CLV Prediction MLOps", layout="wide")

# Initialize BigQuery client for logging
@st.cache_resource
def get_bq_client():
    try:
        return bigquery.Client(project="clv-predictions-mlops")
    except:
        return None

bq_client = get_bq_client()

def log_prediction(features_dict, prediction):
    """Log prediction to BigQuery for monitoring"""
    if bq_client is None:
        return
    try:
        table_id = "clv-predictions-mlops.retail_data.prediction_logs"
        row = {
            "timestamp": datetime.utcnow().isoformat(),
            "recency": features_dict.get("recency", 0),
            "frequency": features_dict.get("frequency", 0),
            "monetary": features_dict.get("monetary", 0),
            "prediction": float(prediction)
        }
        errors = bq_client.insert_rows_json(table_id, [row])
    except Exception as e:
        pass

# Load model, scaler, and baseline features from GCS
@st.cache_resource
def load_artifacts():
    try:
        client = storage.Client()
        bucket = client.bucket("clv-prediction-data")
        
        # Download model
        bucket.blob("models/clv_model_tuned.keras").download_to_filename("/tmp/model.keras")
        model = tf.keras.models.load_model("/tmp/model.keras")
        
        # Download scaler
        bucket.blob("models/clv_scaler.pkl").download_to_filename("/tmp/scaler.pkl")
        scaler = joblib.load("/tmp/scaler.pkl")
        
        # Download feature data for baseline
        bucket.blob("features/clv_features.parquet").download_to_filename("/tmp/features.parquet")
        df = pd.read_parquet("/tmp/features.parquet")
        feature_cols = [c for c in df.columns if c not in ["customer_id", "target_clv"]]
        baseline = df[feature_cols].median().values
        
        return model, scaler, baseline, feature_cols
    except Exception as e:
        st.error(f"Could not load model: {e}")
        return None, None, None, None

model, scaler, baseline_features, feature_cols = load_artifacts()

# Sidebar
st.sidebar.header("Model Info")
st.sidebar.metric("Model Type", "Hybrid NN")
st.sidebar.metric("Median AE", "$429")
st.sidebar.metric("R²", "0.735")

st.sidebar.markdown("---")
st.sidebar.markdown("### Features")
st.sidebar.markdown("""
- 12 numerical features (RFM+)
- 384 text embeddings (Hugging Face)
- Tuned via Vertex AI Vizier
""")

# Main content
st.title("Customer Lifetime Value Prediction")
st.markdown("**MLOps Pipeline Demo** - Hybrid Neural Network with Hugging Face Embeddings")

tab1, tab2, tab3, tab4 = st.tabs(["Predict CLV", "Model Performance", "Feature Importance", "Architecture"])

with tab1:
    st.header("Predict Customer Lifetime Value")
    
    col1, col2 = st.columns(2)
    
    with col1:
        st.subheader("Customer Features")
        
        recency = st.slider("Recency (days since last purchase)", 0, 365, 30)
        frequency = st.slider("Frequency (number of orders)", 1, 50, 25)
        avg_order = st.number_input("Average Order Value $", 0, 5000, 1000)
        tenure = st.slider("Customer Tenure (days)", 0, 365, 180)
        unique_products = st.slider("Unique Products Purchased", 1, 100, 50)
        
        # Calculate monetary from frequency * avg_order
        monetary = frequency * avg_order
        st.caption(f"Calculated Monetary (Frequency × Avg Order): ${monetary:,}")
    
    with col2:
        st.subheader("Prediction")
        
        if st.button("Predict CLV", type="primary"):
            if model is not None and baseline_features is not None:
                # Start with median customer baseline (includes real embeddings)
                features = baseline_features.copy()
                
                # Override with slider values
                if "recency_days" in feature_cols:
                    features[feature_cols.index("recency_days")] = recency
                if "frequency" in feature_cols:
                    features[feature_cols.index("frequency")] = frequency
                if "monetary" in feature_cols:
                    features[feature_cols.index("monetary")] = monetary
                if "avg_order_value" in feature_cols:
                    features[feature_cols.index("avg_order_value")] = avg_order
                if "customer_tenure_days" in feature_cols:
                    features[feature_cols.index("customer_tenure_days")] = tenure
                if "unique_products" in feature_cols:
                    features[feature_cols.index("unique_products")] = unique_products
                
                # Scale and predict with ACTUAL model
                features_scaled = scaler.transform(features.reshape(1, -1))
                prediction = model.predict(features_scaled, verbose=0)[0][0]
                prediction = max(0, prediction)
                
                # Log to BigQuery
                log_prediction({
                    "recency": recency,
                    "frequency": frequency,
                    "monetary": monetary
                }, prediction)
                
                st.metric("Predicted 12-Month CLV", f"${prediction:,.0f}")
                
                # Customer segment
                if prediction > 5000:
                    st.success("🌟 High-Value Customer")
                elif prediction > 1000:
                    st.info("📈 Medium-Value Customer")
                else:
                    st.warning("📊 Low-Value Customer")
            else:
                st.error("Model not loaded")

with tab2:
    st.header("Model Performance")
    
    col1, col2 = st.columns(2)
    
    with col1:
        # Baseline vs Tuned MAE comparison
        tuning_data = {
            "Model": ["Baseline", "Tuned"],
            "MAE ($)": [1987, 1449]
        }
        fig = px.bar(tuning_data, x="Model", y="MAE ($)", 
                     title="Hyperparameter Tuning Impact (27% Improvement)",
                     color="Model", color_discrete_map={"Baseline": "gray", "Tuned": "green"})
        st.plotly_chart(fig, use_container_width=True)
    
    with col2:
        st.markdown("### Performance Metrics")
        st.markdown("""
        | Metric | Value |
        |--------|-------|
        | Median Absolute Error | $429 |
        | R² Score | 0.735 |
        | Predictions within $1,000 | 68.6% |
        """)
        
        st.markdown("### Vizier Tuning")
        st.markdown("""
        - **Trials**: 15
        - **Algorithm**: Random Search
        - **Best params**: 201/74 units, 0.25 dropout, 0.0027 lr
        """)

with tab3:
    st.header("Feature Importance (Integrated Gradients)")
    
    importance_data = {
        "Feature": ["monetary", "unique_purchase_days", "frequency", "orders_per_month", 
                   "total_items_purchased", "unique_products", "avg_order_value", 
                   "customer_tenure_days", "emb_115", "emb_279"],
        "Attribution": [1900, 1350, 1300, 1150, 1100, 1000, 250, 220, 150, 140]
    }
    
    fig = px.bar(importance_data, x="Attribution", y="Feature", orientation="h",
                 title="Top Features Driving CLV Predictions",
                 color="Attribution", color_continuous_scale="greens")
    fig.update_layout(yaxis={"categoryorder": "total ascending"})
    st.plotly_chart(fig, use_container_width=True)
    
    st.markdown("""
    **Key Insights:**
    - **Monetary** (past spend) is the strongest predictor
    - **Engagement metrics** (purchase frequency, unique days) rank highly
    - **Text embeddings** (emb_*) contribute - what customers buy matters
    """)

with tab4:
    st.header("MLOps Architecture")
    
    st.code("""
                           CLV PREDICTION MLOPS PIPELINE

==============================================================================
                                 DATA LAYER
==============================================================================

  +-----------+     +-----------+     +-----------+     +-----------+
  |  BigQuery |---->|  Dataproc |---->|  Hugging  |---->|    GCS    |
  | (Raw Data)|     | (PySpark) |     |   Face    |     |(Features) |
  +-----------+     +-----------+     +-----------+     +-----+-----+
                                                              |
                                                              v
==============================================================================
                                  ML LAYER
==============================================================================

  +-----------+     +-----------+     +-----------+     +-----------+
  |  Vertex   |---->|  Vertex   |---->|   Model   |---->|    GKE    |
  |  Vizier   |     | Pipeline  |     | Registry  |     |  (Prod)   |
  +-----------+     +-----+-----+     +-----+-----+     +-----------+
                          |                 |
                          |                 |           +-----------+
                          |                 +---------->| Cloud Run |
                          |                             |(Demo+A/B) |
                          |                             +-----+-----+
                          |                                   |
                          | Retrain                           |
                          |                                   v
==============================================================================
                             MONITORING LAYER
==============================================================================

  +-----------+     +-----------+     +-----------+     +-----------+
  |   Cloud   |---->| Evidently |---->|   Cloud   |<----|  BigQuery |
  | Scheduler |     |  (Drift)  |     | Function  |     |  (Logs)   |
  +-----------+     +-----------+     +-----+-----+     +-----------+
                                            |
                                            v
                                      +-----------+
                                      |  Vertex   |
                                      | Pipeline  |
                                      +-----------+
    """, language=None)
    
    col1, col2, col3 = st.columns(3)
    
    with col1:
        st.markdown("**Data Layer**")
        st.markdown("- BigQuery (storage)")
        st.markdown("- PySpark (processing)")
        st.markdown("- Hugging Face (embeddings)")
    
    with col2:
        st.markdown("**Deployment**")
        st.markdown("- GKE (production)")
        st.markdown("- Cloud Run (demo + A/B)")
        st.markdown("- Cloud Build CI/CD")
        st.markdown("- Model Registry")
    
    with col3:
        st.markdown("**Monitoring**")
        st.markdown("- Cloud Scheduler")
        st.markdown("- Evidently AI (drift)")
        st.markdown("- Cloud Functions (retrain)")
        st.markdown("- BigQuery (logs)")

# Footer
st.markdown("---")
st.caption("📝 Note: This demo exposes 5 of 396 features. The model uses median customer values as baseline (including 384 Hugging Face text embeddings) and overrides with slider inputs for real-time prediction.")
st.markdown("**Project by Arion Farhi** | [GitHub](https://github.com/arion-farhi)")
'''

with open("streamlit_app/app.py", "w") as f:
    f.write(app_code)

print("Updated app.py with:")
print("  - Average order value default $1000")
print("  - Frequency default 25, unique products default 50")
print("  - Fixed architecture diagram with ASCII box characters")
print("  - Added Cloud Build CI/CD to tech stack")

Updated app.py with:
  - Average order value default $1000
  - Frequency default 25, unique products default 50
  - Fixed architecture diagram with ASCII box characters
  - Added Cloud Build CI/CD to tech stack


In [25]:
!gcloud builds submit streamlit_app \
    --tag gcr.io/{PROJECT_ID}/clv-demo \
    --project={PROJECT_ID}

!gcloud run deploy clv-demo \
    --image gcr.io/{PROJECT_ID}/clv-demo \
    --platform managed \
    --region {REGION} \
    --allow-unauthenticated \
    --memory 2Gi \
    --project={PROJECT_ID}

!gcloud run services update-traffic clv-demo \
    --region={REGION} \
    --to-latest \
    --project={PROJECT_ID}

Creating temporary archive of 3 file(s) totalling 11.6 KiB before compression.
Uploading tarball of [streamlit_app] to [gs://clv-predictions-mlops_cloudbuild/source/1765506757.874213-98f026b64e7241bf911c20db9d385858.tgz]
Created [https://cloudbuild.googleapis.com/v1/projects/clv-predictions-mlops/locations/global/builds/431b9f01-495a-4c57-a746-1566f990740f].
Logs are available at [ https://console.cloud.google.com/cloud-build/builds/431b9f01-495a-4c57-a746-1566f990740f?project=674754622820 ].
Waiting for build to complete. Polling interval: 1 second(s).
----------------------------- REMOTE BUILD OUTPUT ------------------------------
starting build "431b9f01-495a-4c57-a746-1566f990740f"

FETCHSOURCE
Fetching storage object: gs://clv-predictions-mlops_cloudbuild/source/1765506757.874213-98f026b64e7241bf911c20db9d385858.tgz#1765506758044318
Copying gs://clv-predictions-mlops_cloudbuild/source/1765506757.874213-98f026b64e7241bf911c20db9d385858.tgz#1765506758044318...
/ [1 files][  3.8 KiB/

In [ ]:
# Check if BigQuery table exists and has data
!bq query --use_legacy_sql=false "SELECT * FROM \`clv-predictions-mlops.retail_data.prediction_logs\` LIMIT 10"